# Characterizing the general methylation landscape

In this notebook, I will characterize the general methylation landscape for each sex separately. To characterize CpG methylation, I will use individual samples, as well as a union BEDgraph that concatenates all sample information.

1. Concatenate coverage information
2. Characterize methylation for each CpG dinucleotide in individual samples and union BEDgraph
2. Determine genomic location of highly methylated, moderately methylated, and lowly CpGs

## 0. Set working directory

In [1]:
!pwd

/Users/yaaminivenkataraman/Documents/ceabigr/code


In [2]:
cd ../output/

/Users/yaaminivenkataraman/Documents/ceabigr/output


In [3]:
!mkdir methylation-landscape

mkdir: methylation-landscape: File exists


In [3]:
cd methylation-landscape/

/Users/yaaminivenkataraman/Documents/ceabigr/output/methylation-landscape


In [4]:
bedtoolsDirectory = "/opt/homebrew/bin/"

In [5]:
#Install pandas for this notebook
import pandas as pd
print(pd.__version__)

0.25.1


## 1. Set up analysis

### 1a. Obtain sample bedGraphs

In [41]:
#Download 10x bedgraphs
!wget -r \
--no-check-certificate --no-directories --no-parent --reject "index.html*" \
-P . \
-A "*10x.bedgraph" https://gannet.fish.washington.edu/seashell/bu-mox/scrubbed/120321-cvBS/

--2022-02-21 14:45:35--  https://gannet.fish.washington.edu/seashell/bu-mox/scrubbed/120321-cvBS/
Resolving gannet.fish.washington.edu (gannet.fish.washington.edu)... 128.95.149.52
Connecting to gannet.fish.washington.edu (gannet.fish.washington.edu)|128.95.149.52|:443... connected.
  Unable to locally verify the issuer's authority.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: ‘./index.html.tmp’

index.html.tmp          [ <=>                ]  62.99K  --.-KB/s    in 0.03s   

2022-02-21 14:45:41 (2.27 MB/s) - ‘./index.html.tmp’ saved [64500]

Loading robots.txt; please ignore errors.
--2022-02-21 14:45:41--  https://gannet.fish.washington.edu/robots.txt
Reusing existing connection to gannet.fish.washington.edu:443.
HTTP request sent, awaiting response... 404 Not Found
2022-02-21 14:45:41 ERROR 404: Not Found.

Removing ./index.html.tmp since it should be rejected.

--2022-02-21 14:45:41--  https://gannet.fish.washington.edu/seashell/bu-mox/s

HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: ‘./index.html?C=S;O=D.tmp’

index.html?C=S;O=D.     [ <=>                ]  62.99K  --.-KB/s    in 0.03s   

2022-02-21 15:03:49 (2.12 MB/s) - ‘./index.html?C=S;O=D.tmp’ saved [64500]

Removing ./index.html?C=S;O=D.tmp since it should be rejected.

--2022-02-21 15:03:49--  https://gannet.fish.washington.edu/seashell/bu-mox/scrubbed/120321-cvBS/?C=D;O=D
Reusing existing connection to gannet.fish.washington.edu:443.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: ‘./index.html?C=D;O=D.tmp’

index.html?C=D;O=D.     [ <=>                ]  62.99K  --.-KB/s    in 0.03s   

2022-02-21 15:03:52 (2.11 MB/s) - ‘./index.html?C=D;O=D.tmp’ saved [64500]

Removing ./index.html?C=D;O=D.tmp since it should be rejected.

FINISHED --2022-02-21 15:03:52--
Total wall clock time: 18m 17s
Downloaded: 35 files, 7.6G in 17m 26s (7.44 MB/s)


In [42]:
#Check directory for all files
!ls

12M_R1_val_1_10x.bedgraph 36F_R1_val_1_10x.bedgraph 54F_R1_val_1_10x.bedgraph
13M_R1_val_1_10x.bedgraph 39F_R1_val_1_10x.bedgraph 59M_R1_val_1_10x.bedgraph
16F_R1_val_1_10x.bedgraph 3F_R1_val_1_10x.bedgraph  64M_R1_val_1_10x.bedgraph
19F_R1_val_1_10x.bedgraph 41F_R1_val_1_10x.bedgraph 6M_R1_val_1_10x.bedgraph
22F_R1_val_1_10x.bedgraph 44F_R1_val_1_10x.bedgraph 76F_R1_val_1_10x.bedgraph
23M_R1_val_1_10x.bedgraph 48M_R1_val_1_10x.bedgraph 77F_R1_val_1_10x.bedgraph
29F_R1_val_1_10x.bedgraph 50F_R1_val_1_10x.bedgraph 7M_R1_val_1_10x.bedgraph
31M_R1_val_1_10x.bedgraph 52F_R1_val_1_10x.bedgraph 9M_R1_val_1_10x.bedgraph
35F_R1_val_1_10x.bedgraph 53F_R1_val_1_10x.bedgraph


In [43]:
#Obtain md5
!md5 *

MD5 (12M_R1_val_1_10x.bedgraph) = 23710e666ba1d8d0aff05465a7ec143d
MD5 (13M_R1_val_1_10x.bedgraph) = 895d0b04d434e9567e648689e734308e
MD5 (16F_R1_val_1_10x.bedgraph) = 5e031b5c1aac89336d1a1a32c84383ff
MD5 (19F_R1_val_1_10x.bedgraph) = ad8e874af92071a08a9fc0e5cd31c959
MD5 (22F_R1_val_1_10x.bedgraph) = a34054b0cedf5b219e1a7f236571f882
MD5 (23M_R1_val_1_10x.bedgraph) = 8b5aa08e26db26865b35090e69c27ce0
MD5 (29F_R1_val_1_10x.bedgraph) = cda12bdb3ac9a2a304005d496c8d641b
MD5 (31M_R1_val_1_10x.bedgraph) = 6ea9d16b7c88775863e5f890144d900b
MD5 (35F_R1_val_1_10x.bedgraph) = fc230a6475afe86a21a99f70ddd51012
MD5 (36F_R1_val_1_10x.bedgraph) = bb83960173d236e832183e7b7a641156
MD5 (39F_R1_val_1_10x.bedgraph) = de0e77ea6da72f370dca9d5b09d7b1f3
MD5 (3F_R1_val_1_10x.bedgraph) = 7be44c21611319f59cfa94eec5a84851
MD5 (41F_R1_val_1_10x.bedgraph) = c3e39faa21463fdecafd78eb6f17b51a
MD5 (44F_R1_val_1_10x.bedgraph) = cd82809a568298c8cc84f7c8ab0a1fa7
MD5 (48M_R1_val_1_10x.bedgraph) = beeb7af3ab210324b787e6b50eed5

In [44]:
%%bash

for f in *10x.bedgraph
do
/opt/homebrew/bin/sortBed \
-i ${f} \
> $(basename ${f%_10x.bedgraph})_10x.sort.bedgraph
done

In [6]:
!ls *sort*

12M_R1_val_1_10x.sort.bedgraph 44F_R1_val_1_10x.sort.bedgraph
13M_R1_val_1_10x.sort.bedgraph 48M_R1_val_1_10x.sort.bedgraph
16F_R1_val_1_10x.sort.bedgraph 50F_R1_val_1_10x.sort.bedgraph
19F_R1_val_1_10x.sort.bedgraph 52F_R1_val_1_10x.sort.bedgraph
22F_R1_val_1_10x.sort.bedgraph 53F_R1_val_1_10x.sort.bedgraph
23M_R1_val_1_10x.sort.bedgraph 54F_R1_val_1_10x.sort.bedgraph
29F_R1_val_1_10x.sort.bedgraph 59M_R1_val_1_10x.sort.bedgraph
31M_R1_val_1_10x.sort.bedgraph 64M_R1_val_1_10x.sort.bedgraph
35F_R1_val_1_10x.sort.bedgraph 6M_R1_val_1_10x.sort.bedgraph
36F_R1_val_1_10x.sort.bedgraph 76F_R1_val_1_10x.sort.bedgraph
39F_R1_val_1_10x.sort.bedgraph 77F_R1_val_1_10x.sort.bedgraph
3F_R1_val_1_10x.sort.bedgraph  7M_R1_val_1_10x.sort.bedgraph
41F_R1_val_1_10x.sort.bedgraph 9M_R1_val_1_10x.sort.bedgraph


### 1b. Remove C->T SNPs

For each sample, I will use BS-Snper output to change the percent methylation for a C->T SNP to 0.

In [46]:
#Download 10x SNP
!wget -r \
--no-check-certificate --no-directories --no-parent --reject "index.html*" \
-P . \
-A "*vcf" https://gannet.fish.washington.edu/seashell/bu-github/nb-2022/C_virginica/analyses/bsnp02/

--2022-02-21 15:07:09--  https://gannet.fish.washington.edu/seashell/bu-github/nb-2022/C_virginica/analyses/bsnp02/
Resolving gannet.fish.washington.edu (gannet.fish.washington.edu)... 128.95.149.52
Connecting to gannet.fish.washington.edu (gannet.fish.washington.edu)|128.95.149.52|:443... connected.
  Unable to locally verify the issuer's authority.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: ‘./index.html.tmp’

index.html.tmp          [ <=>                ]  32.59K  --.-KB/s    in 0.02s   

2022-02-21 15:07:11 (1.89 MB/s) - ‘./index.html.tmp’ saved [33377]

Loading robots.txt; please ignore errors.
--2022-02-21 15:07:11--  https://gannet.fish.washington.edu/robots.txt
Reusing existing connection to gannet.fish.washington.edu:443.
HTTP request sent, awaiting response... 404 Not Found
2022-02-21 15:07:11 ERROR 404: Not Found.

Removing ./index.html.tmp since it should be rejected.

--2022-02-21 15:07:11--  https://gannet.fish.washington.edu

HTTP request sent, awaiting response... 200 OK
Length: 537035183 (512M) [text/x-vcard]
Saving to: ‘./23M_R1_val_1_bismark_bt2_pe.SNP-results.vcf’

23M_R1_val_1_bismar 100%[===================>] 512.16M  7.35MB/s    in 70s     

2022-02-21 15:17:44 (7.32 MB/s) - ‘./23M_R1_val_1_bismark_bt2_pe.SNP-results.vcf’ saved [537035183/537035183]

--2022-02-21 15:17:44--  https://gannet.fish.washington.edu/seashell/bu-github/nb-2022/C_virginica/analyses/bsnp02/29F_R1_val_1_bismark_bt2_pe.SNP-results.vcf
Reusing existing connection to gannet.fish.washington.edu:443.
HTTP request sent, awaiting response... 200 OK
Length: 492776744 (470M) [text/x-vcard]
Saving to: ‘./29F_R1_val_1_bismark_bt2_pe.SNP-results.vcf’

29F_R1_val_1_bismar 100%[===================>] 469.95M  8.65MB/s    in 55s     

2022-02-21 15:18:39 (8.49 MB/s) - ‘./29F_R1_val_1_bismark_bt2_pe.SNP-results.vcf’ saved [492776744/492776744]

--2022-02-21 15:18:39--  https://gannet.fish.washington.edu/seashell/bu-github/nb-2022/C_virginica/a

HTTP request sent, awaiting response... 200 OK
Length: 494986093 (472M) [text/x-vcard]
Saving to: ‘./76F_R1_val_1_bismark_bt2_pe.SNP-results.vcf’

76F_R1_val_1_bismar 100%[===================>] 472.05M  7.76MB/s    in 53s     

2022-02-21 15:31:35 (8.92 MB/s) - ‘./76F_R1_val_1_bismark_bt2_pe.SNP-results.vcf’ saved [494986093/494986093]

--2022-02-21 15:31:35--  https://gannet.fish.washington.edu/seashell/bu-github/nb-2022/C_virginica/analyses/bsnp02/77F_R1_val_1_bismark_bt2_pe.SNP-results.vcf
Reusing existing connection to gannet.fish.washington.edu:443.
HTTP request sent, awaiting response... 200 OK
Length: 518123700 (494M) [text/x-vcard]
Saving to: ‘./77F_R1_val_1_bismark_bt2_pe.SNP-results.vcf’

77F_R1_val_1_bismar 100%[===================>] 494.12M  7.94MB/s    in 57s     

2022-02-21 15:32:33 (8.60 MB/s) - ‘./77F_R1_val_1_bismark_bt2_pe.SNP-results.vcf’ saved [518123700/518123700]

--2022-02-21 15:32:33--  https://gannet.fish.washington.edu/seashell/bu-github/nb-2022/C_virginica/a

In [28]:
%%bash

for f in *10x.sort.bedgraph
do
awk -F"\t" 'NR==FNR{a[$1"\t"$2]=$1"\t"$2;next}{if(($1"\t"$2) in a) print $1"\t"$2"\t"$3"\t"0;else print $0}' \
$(basename ${f%_10x.sort.bedgraph})_bismark_bt2_pe.SNP-results.vcf \
${f} \
> $(basename ${f%_10x.sort.bedgraph})_10x.SNPcorr.bedgraph
done

In [7]:
!ls *10x.SNPcorr.bedgraph

12M_R1_val_1_10x.SNPcorr.bedgraph 44F_R1_val_1_10x.SNPcorr.bedgraph
13M_R1_val_1_10x.SNPcorr.bedgraph 48M_R1_val_1_10x.SNPcorr.bedgraph
16F_R1_val_1_10x.SNPcorr.bedgraph 50F_R1_val_1_10x.SNPcorr.bedgraph
19F_R1_val_1_10x.SNPcorr.bedgraph 52F_R1_val_1_10x.SNPcorr.bedgraph
22F_R1_val_1_10x.SNPcorr.bedgraph 53F_R1_val_1_10x.SNPcorr.bedgraph
23M_R1_val_1_10x.SNPcorr.bedgraph 54F_R1_val_1_10x.SNPcorr.bedgraph
29F_R1_val_1_10x.SNPcorr.bedgraph 59M_R1_val_1_10x.SNPcorr.bedgraph
31M_R1_val_1_10x.SNPcorr.bedgraph 64M_R1_val_1_10x.SNPcorr.bedgraph
35F_R1_val_1_10x.SNPcorr.bedgraph 6M_R1_val_1_10x.SNPcorr.bedgraph
36F_R1_val_1_10x.SNPcorr.bedgraph 76F_R1_val_1_10x.SNPcorr.bedgraph
39F_R1_val_1_10x.SNPcorr.bedgraph 77F_R1_val_1_10x.SNPcorr.bedgraph
3F_R1_val_1_10x.SNPcorr.bedgraph  7M_R1_val_1_10x.SNPcorr.bedgraph
41F_R1_val_1_10x.SNPcorr.bedgraph 9M_R1_val_1_10x.SNPcorr.bedgraph


In [44]:
%%bash

for f in *10x.sort.bedgraph
do
/opt/homebrew/bin/intersectBed \
-wa \
-a ${f} \
-b $(basename ${f%_10x.sort.bedgraph})_bismark_bt2_pe.SNP-results.vcf \
> $(basename ${f%_10x.sort.bedgraph})_10x.SNPcorr.changedpos.bedgraph
done

## 2. General methylation landscape

### 2a. Create a union BEDgraph

I will use `unionBedGraphs` to concatenate information for all loci across samples. This will be use in separate analyses.

In [8]:
!{bedtoolsDirectory}unionBedGraphs -h


Tool:    bedtools unionbedg (aka unionBedGraphs)
Version: v2.30.0
Summary: Combines multiple BedGraph files into a single file,
	 allowing coverage comparisons between them.

Usage:   bedtools unionbedg [OPTIONS] -i FILE1 FILE2 .. FILEn
	 Assumes that each BedGraph file is sorted by chrom/start 
	 and that the intervals in each are non-overlapping.

Options: 
	-header		Print a header line.
			(chrom/start/end + names of each file).

	-names		A list of names (one/file) to describe each file in -i.
			These names will be printed in the header line.

	-g		Use genome file to calculate empty regions.
			- STRING.

	-empty		Report empty regions (i.e., start/end intervals w/o
			values in all files).
			- Requires the '-g FILE' parameter.

	-filler TEXT	Use TEXT when representing intervals having no value.
			- Default is '0', but you can use 'N/A' or any text.

	-examples	Show detailed usage examples.



In [29]:
#Create union BEDgraph from sorted files
#Include a header
#Use N/A when there is no data for a CpG in a sample
#Define sample IDs
#Use sorted bedgraphs
#Save output
!{bedtoolsDirectory}unionBedGraphs \
-header \
-filler N/A \
-names 12M 13M 16F 19F 22F 23M 29F 31M 35F 36F 39F 3F 41F 44F 48M 50F 52F 53F 54F 59M 64M 6M 76F 77F 7M 9M \
-i \
*10x.SNPcorr.bedgraph \
> union_10x.bedgraph

In [30]:
#Check output
!head union_10x.bedgraph
!wc -l union_10x.bedgraph

chrom	start	end	12M	13M	16F	19F	22F	23M	29F	31M	35F	36F	39F	3F	41F	44F	48M	50F	52F	53F	54F	59M	64M	6M	76F	77F	7M	9M
NC_007175.2	48	50	0.000000	0.000000	1.923077	0.731452	1.015228	0.000000	1.444623	3.125000	0.844511	1.699182	0.541339	1.694915	1.928375	2.136076	1.086957	1.672640	1.806240	1.100917	1.780694	0.000000	3.973510	0.653595	0.682057	1.661475	3.750000	1.754386
NC_007175.2	50	52	0.000000	0.000000	1.626016	0.733855	1.507937	0.000000	1.349325	1.470588	0.600462	1.700880	0.599908	1.500000	2.570694	1.327434	1.036269	1.874311	1.371951	1.069218	1.842105	0.000000	3.797468	0.632911	0.442478	1.439539	3.488372	1.666667
NC_007175.2	87	89	1.169591	1.293103	1.045857	0.286907	0.789771	0.990099	0.859599	0.671141	0.666349	0.813008	0.444115	1.284875	0.800915	1.361796	0.245700	0.959596	0.852273	0.758853	0.866927	0.000000	0.319489	0.666667	0.208008	1.021477	0.478469	0.000000
NC_007175.2	146	148	1.261830	0.461894	1.502146	0.684369	1.081187	0.819672	1.183206	0.332226	0.721028	1.522344	0.562023	0.995025	

### 2b. Manipulate with `pandas`

In [31]:
#Import union data into pandas
#Check head
df = pd.read_table("union_10x.bedgraph")
df.head(5)

chrom  start  end       12M       13M       16F       19F       22F  \
0  NC_007175.2     48   50  0.000000  0.000000  1.923077  0.731452  1.015228   
1  NC_007175.2     50   52  0.000000  0.000000  1.626016  0.733855  1.507937   
2  NC_007175.2     87   89  1.169591  1.293103  1.045857  0.286907  0.789771   
3  NC_007175.2    146  148  1.261830  0.461894  1.502146  0.684369  1.081187   
4  NC_007175.2    192  194  1.129944  1.271186  1.726908  0.691776  1.094563   

        23M       29F  ...       52F       53F       54F      59M       64M  \
0  0.000000  1.444623  ...  1.806240  1.100917  1.780694  0.00000  3.973510   
1  0.000000  1.349325  ...  1.371951  1.069218  1.842105  0.00000  3.797468   
2  0.990099  0.859599  ...  0.852273  0.758853  0.866927  0.00000  0.319489   
3  0.819672  1.183206  ...  1.306458  1.210914  0.924855  0.00000  2.027027   
4  1.955990  1.097734  ...  1.486346  1.194200  0.896287  0.47619  1.369863   

         6M       76F       77F        7M        9M  
0  0.653595  0.682057  1.661475  3.750000  1.754386  
1  0.632911  0.442478  1.439539  3.488372  1.666667  
2  0.666667  0.208008  1.021477  0.478469  0.000000  
3  0.702988  0.475325  1.308017  1.566580  0.456621  
4  0.161031  0.558659  1.286383  2.195122  0.840336  

[5 rows x 29 columns]

In [32]:
#Average all samples for total genome methylation information and save as a new column
#NA are not included in averages
#Check output
df['total'] = df[['12M', '13M', '16F', '19F', '22F', '23M', '29F', '31M', '35F', '36F', '39F', '3F', '41F', '44F', '48M', '50F', '52F', '53F', '54F', '59M', '64M', '6M', '76F', '77F', '7M', '9M']].mean(axis=1)
df.tail(10)

chrom     start       end  12M  13M  16F  19F  22F  23M  29F  \
12951894  NC_035789.1  32649654  32649656  0.0  0.0  0.0  NaN  NaN  NaN  0.0   
12951895  NC_035789.1  32649732  32649734  0.0  0.0  0.0  NaN  NaN  NaN  0.0   
12951896  NC_035789.1  32649736  32649738  0.0  0.0  0.0  NaN  NaN  NaN  0.0   
12951897  NC_035789.1  32649799  32649801  NaN  0.0  NaN  NaN  NaN  NaN  NaN   
12951898  NC_035789.1  32649876  32649878  0.0  0.0  0.0  NaN  0.0  NaN  0.0   
12951899  NC_035789.1  32649885  32649887  0.0  0.0  0.0  NaN  0.0  NaN  0.0   
12951900  NC_035789.1  32649895  32649897  0.0  0.0  0.0  NaN  0.0  NaN  0.0   
12951901  NC_035789.1  32649930  32649932  NaN  0.0  NaN  NaN  0.0  NaN  NaN   
12951902  NC_035789.1  32649933  32649935  NaN  0.0  NaN  NaN  0.0  NaN  NaN   
12951903  NC_035789.1  32649966  32649968  NaN  0.0  NaN  NaN  0.0  NaN  NaN   

          ...  53F  54F  59M  64M   6M  76F  77F   7M  9M  total  
12951894  ...  NaN  NaN  0.0  NaN  0.0  0.0  0.0  0.0 NaN    0.0  
12951895  ...  0.0  NaN  NaN  NaN  0.0  NaN  0.0  0.0 NaN    0.0  
12951896  ...  0.0  NaN  NaN  NaN  0.0  NaN  0.0  0.0 NaN    0.0  
12951897  ...  NaN  0.0  NaN  NaN  NaN  NaN  NaN  NaN NaN    0.0  
12951898  ...  NaN  0.0  0.0  NaN  0.0  0.0  0.0  0.0 NaN    0.0  
12951899  ...  NaN  0.0  0.0  NaN  0.0  0.0  0.0  0.0 NaN    0.0  
12951900  ...  NaN  0.0  0.0  NaN  0.0  0.0  0.0  0.0 NaN    0.0  
12951901  ...  NaN  0.0  0.0  NaN  0.0  NaN  0.0  NaN NaN    0.0  
12951902  ...  NaN  0.0  0.0  0.0  0.0  NaN  0.0  NaN NaN    0.0  
12951903  ...  NaN  0.0  0.0  0.0  NaN  NaN  0.0  NaN NaN    0.0  

[10 rows x 30 columns]

In [33]:
#Save dataframe in a tabular format and include N/As. Do not include quotes.
df.to_csv("union-averages_10x.bedgraph", sep = "\t", na_rep = "N/A", quoting = 3)

In [34]:
#Check pandas manipulations
!tail union-averages_10x.bedgraph

12951894	NC_035789.1	32649654	32649656	0.0	0.0	0.0	N/A	N/A	N/A	0.0	N/A	N/A	0.0	N/A	0.0	N/A	N/A	0.0	0.0	N/A	N/A	N/A	0.0	N/A	0.0	0.0	0.0	0.0	N/A	0.0
12951895	NC_035789.1	32649732	32649734	0.0	0.0	0.0	N/A	N/A	N/A	0.0	N/A	N/A	N/A	N/A	0.0	N/A	N/A	0.0	N/A	N/A	0.0	N/A	N/A	N/A	0.0	N/A	0.0	0.0	N/A	0.0
12951896	NC_035789.1	32649736	32649738	0.0	0.0	0.0	N/A	N/A	N/A	0.0	N/A	N/A	N/A	N/A	0.0	N/A	N/A	0.0	N/A	N/A	0.0	N/A	N/A	N/A	0.0	N/A	0.0	0.0	N/A	0.0
12951897	NC_035789.1	32649799	32649801	N/A	0.0	N/A	N/A	N/A	N/A	N/A	N/A	0.0	N/A	N/A	0.0	N/A	N/A	N/A	N/A	N/A	N/A	0.0	N/A	N/A	N/A	N/A	N/A	N/A	N/A	0.0
12951898	NC_035789.1	32649876	32649878	0.0	0.0	0.0	N/A	0.0	N/A	0.0	N/A	0.0	0.0	N/A	0.0	N/A	N/A	N/A	0.0	0.0	N/A	0.0	0.0	N/A	0.0	0.0	0.0	0.0	N/A	0.0
12951899	NC_035789.1	32649885	32649887	0.0	0.0	0.0	N/A	0.0	N/A	0.0	N/A	0.0	0.0	N/A	0.0	N/A	N/A	N/A	0.0	0.0	N/A	0.0	0.0	N/A	0.0	0.0	0.0	0.0	N/A	0.0
12951900	NC_035789.1	32649895	32649897	0.0	0.0	0.0	N/A	0.0	N/A	0.0	N/A	0.0	0.0	N/A	0.0	N/A	N/A	N/A	0.0	0.0	N/A	0.0	0.0

## 3. Sex-specific methylation landscape

### 3a. Female

In [9]:
!ls *F*10x.SNPcorr.bedgraph

16F_R1_val_1_10x.SNPcorr.bedgraph 41F_R1_val_1_10x.SNPcorr.bedgraph
19F_R1_val_1_10x.SNPcorr.bedgraph 44F_R1_val_1_10x.SNPcorr.bedgraph
22F_R1_val_1_10x.SNPcorr.bedgraph 50F_R1_val_1_10x.SNPcorr.bedgraph
29F_R1_val_1_10x.SNPcorr.bedgraph 52F_R1_val_1_10x.SNPcorr.bedgraph
35F_R1_val_1_10x.SNPcorr.bedgraph 53F_R1_val_1_10x.SNPcorr.bedgraph
36F_R1_val_1_10x.SNPcorr.bedgraph 54F_R1_val_1_10x.SNPcorr.bedgraph
39F_R1_val_1_10x.SNPcorr.bedgraph 76F_R1_val_1_10x.SNPcorr.bedgraph
3F_R1_val_1_10x.SNPcorr.bedgraph  77F_R1_val_1_10x.SNPcorr.bedgraph


In [35]:
#Create union BEDgraph from sorted files
#Include a header
#Use N/A when there is no data for a CpG in a sample
#Define sample IDs
#Use sorted bedgraphs
#Save output
!{bedtoolsDirectory}unionBedGraphs \
-header \
-filler N/A \
-names 16F 19F 22F 29F 35F 36F 39F 3F 41F 44F 50F 52F 53F 54F 76F 77F \
-i \
*F*10x.SNPcorr.bedgraph \
> fem-union_10x.bedgraph

In [36]:
#Check output
!head fem-union_10x.bedgraph
!wc -l fem-union_10x.bedgraph

chrom	start	end	16F	19F	22F	29F	35F	36F	39F	3F	41F	44F	50F	52F	53F	54F	76F	77F
NC_007175.2	48	50	1.923077	0.731452	1.015228	1.444623	0.844511	1.699182	0.541339	1.694915	1.928375	2.136076	1.672640	1.806240	1.100917	1.780694	0.682057	1.661475
NC_007175.2	50	52	1.626016	0.733855	1.507937	1.349325	0.600462	1.700880	0.599908	1.500000	2.570694	1.327434	1.874311	1.371951	1.069218	1.842105	0.442478	1.439539
NC_007175.2	87	89	1.045857	0.286907	0.789771	0.859599	0.666349	0.813008	0.444115	1.284875	0.800915	1.361796	0.959596	0.852273	0.758853	0.866927	0.208008	1.021477
NC_007175.2	146	148	1.502146	0.684369	1.081187	1.183206	0.721028	1.522344	0.562023	0.995025	1.548541	1.321760	1.619645	1.306458	1.210914	0.924855	0.475325	1.308017
NC_007175.2	192	194	1.726908	0.691776	1.094563	1.097734	0.996997	1.613626	0.538915	1.198820	1.716501	1.497326	1.575555	1.486346	1.194200	0.896287	0.558659	1.286383
NC_007175.2	245	247	1.228250	0.414110	0.794148	1.226456	0.824253	1.138753	0.516834	1.106095	1.192146	1.2878

In [85]:
#Import union data into pandas
#Check head
df = pd.read_table("fem-union_10x.bedgraph")
df.head(5)

chrom  start  end       16F       19F       22F       29F       35F  \
0  NC_007175.2     48   50  1.923077  0.731452  1.015228  1.444623  0.844511   
1  NC_007175.2     50   52  1.626016  0.733855  1.507937  1.349325  0.600462   
2  NC_007175.2     87   89  1.045857  0.286907  0.789771  0.859599  0.666349   
3  NC_007175.2    146  148  1.502146  0.684369  1.081187  1.183206  0.721028   
4  NC_007175.2    192  194  1.726908  0.691776  1.094563  1.097734  0.996997   

        36F       39F        3F       41F       44F       50F       52F  \
0  1.699182  0.541339  1.694915  1.928375  2.136076  1.672640  1.806240   
1  1.700880  0.599908  1.500000  2.570694  1.327434  1.874311  1.371951   
2  0.813008  0.444115  1.284875  0.800915  1.361796  0.959596  0.852273   
3  1.522344  0.562023  0.995025  1.548541  1.321760  1.619645  1.306458   
4  1.613626  0.538915  1.198820  1.716501  1.497326  1.575555  1.486346   

        53F       54F       76F       77F  
0  1.100917  1.780694  0.682057  1.661475  
1  1.069218  1.842105  0.442478  1.439539  
2  0.758853  0.866927  0.208008  1.021477  
3  1.210914  0.924855  0.475325  1.308017  
4  1.194200  0.896287  0.558659  1.286383

In [95]:
#Average all samples for total genome methylation information and save as a new column
#NA are not included in averages
#Check output
df['average'] = df[['16F', '19F', '22F', '29F', '35F', '36F', '39F', '3F', '41F', '44F', '50F', '52F', '53F', '54F', '76F', '77F']].mean(axis=1)
df.tail(10)

chrom     start       end  16F  19F  22F  29F  35F  36F  39F  \
12678561  NC_035789.1  32649654  32649656  0.0  NaN  NaN  0.0  NaN  0.0  NaN   
12678562  NC_035789.1  32649732  32649734  0.0  NaN  NaN  0.0  NaN  NaN  NaN   
12678563  NC_035789.1  32649736  32649738  0.0  NaN  NaN  0.0  NaN  NaN  NaN   
12678564  NC_035789.1  32649799  32649801  NaN  NaN  NaN  NaN  0.0  NaN  NaN   
12678565  NC_035789.1  32649876  32649878  0.0  NaN  0.0  0.0  0.0  0.0  NaN   
12678566  NC_035789.1  32649885  32649887  0.0  NaN  0.0  0.0  0.0  0.0  NaN   
12678567  NC_035789.1  32649895  32649897  0.0  NaN  0.0  0.0  0.0  0.0  NaN   
12678568  NC_035789.1  32649930  32649932  NaN  NaN  0.0  NaN  0.0  NaN  NaN   
12678569  NC_035789.1  32649933  32649935  NaN  NaN  0.0  NaN  0.0  NaN  NaN   
12678570  NC_035789.1  32649966  32649968  NaN  NaN  0.0  NaN  0.0  NaN  NaN   

          ...  41F  44F  50F  52F  53F  54F  76F  77F  total  average  
12678561  ...  NaN  NaN  0.0  NaN  NaN  NaN  0.0  0.0    0.0      0.0  
12678562  ...  NaN  NaN  NaN  NaN  0.0  NaN  NaN  0.0    0.0      0.0  
12678563  ...  NaN  NaN  NaN  NaN  0.0  NaN  NaN  0.0    0.0      0.0  
12678564  ...  NaN  NaN  NaN  NaN  NaN  0.0  NaN  NaN    0.0      0.0  
12678565  ...  NaN  NaN  0.0  0.0  NaN  0.0  0.0  0.0    0.0      0.0  
12678566  ...  NaN  NaN  0.0  0.0  NaN  0.0  0.0  0.0    0.0      0.0  
12678567  ...  NaN  NaN  0.0  0.0  NaN  0.0  0.0  0.0    0.0      0.0  
12678568  ...  NaN  NaN  NaN  0.0  NaN  0.0  NaN  0.0    0.0      0.0  
12678569  ...  NaN  NaN  NaN  0.0  NaN  0.0  NaN  0.0    0.0      0.0  
12678570  ...  NaN  NaN  NaN  NaN  NaN  0.0  NaN  0.0    0.0      0.0  

[10 rows x 21 columns]

In [105]:
#Save dataframe in a tabular format and include N/As. Do not include quotes.
df.to_csv("fem-union-averages.bedgraph", sep = "\t", na_rep = "N/A", quoting = 3)

In [106]:
#Check pandas manipulations
!tail fem-union-averages.bedgraph

12678561	NC_035789.1	32649654	32649656	0.0	N/A	N/A	0.0	N/A	0.0	N/A	0.0	N/A	N/A	0.0	N/A	N/A	N/A	0.0	0.0	0.0	0.0
12678562	NC_035789.1	32649732	32649734	0.0	N/A	N/A	0.0	N/A	N/A	N/A	0.0	N/A	N/A	N/A	N/A	0.0	N/A	N/A	0.0	0.0	0.0
12678563	NC_035789.1	32649736	32649738	0.0	N/A	N/A	0.0	N/A	N/A	N/A	0.0	N/A	N/A	N/A	N/A	0.0	N/A	N/A	0.0	0.0	0.0
12678564	NC_035789.1	32649799	32649801	N/A	N/A	N/A	N/A	0.0	N/A	N/A	0.0	N/A	N/A	N/A	N/A	N/A	0.0	N/A	N/A	0.0	0.0
12678565	NC_035789.1	32649876	32649878	0.0	N/A	0.0	0.0	0.0	0.0	N/A	0.0	N/A	N/A	0.0	0.0	N/A	0.0	0.0	0.0	0.0	0.0
12678566	NC_035789.1	32649885	32649887	0.0	N/A	0.0	0.0	0.0	0.0	N/A	0.0	N/A	N/A	0.0	0.0	N/A	0.0	0.0	0.0	0.0	0.0
12678567	NC_035789.1	32649895	32649897	0.0	N/A	0.0	0.0	0.0	0.0	N/A	0.0	N/A	N/A	0.0	0.0	N/A	0.0	0.0	0.0	0.0	0.0
12678568	NC_035789.1	32649930	32649932	N/A	N/A	0.0	N/A	0.0	N/A	N/A	0.0	N/A	N/A	N/A	0.0	N/A	0.0	N/A	0.0	0.0	0.0
12678569	NC_035789.1	32649933	32649935	N/A	N/A	0.0	N/A	0.0	N/A	N/A	0.0	N/A	N/A	N/A	0.0	N/A	0.0	N/A	0.0	0.0	0.0
1

In [117]:
#Print chr, start, end, and average columns
#Remove header
!awk '{print $2"\t"$3"\t"$4"\t"$21}' fem-union-averages.bedgraph \
| tail -n +2 \
> fem-union-averages_10x.SNPcorr.bedgraph

In [118]:
!head fem-union-averages_10x.SNPcorr.bedgraph

NC_007175.2	48	50	1.4164250624999999
NC_007175.2	50	52	1.3472570625
NC_007175.2	87	89	0.813770375
NC_007175.2	146	148	1.1229276875
NC_007175.2	192	194	1.19816225
NC_007175.2	245	247	0.9728829374999999
NC_007175.2	256	258	1.0959236250000002
NC_007175.2	263	265	1.0578576875
NC_007175.2	265	267	1.0646793125
NC_007175.2	331	333	1.1050068124999999


### 3b. Male methylation landscape

In [43]:
#Create union BEDgraph from sorted files
#Include a header
#Use N/A when there is no data for a CpG in a sample
#Define sample IDs
#Use sorted bedgraphs
#Save output
!{bedtoolsDirectory}unionBedGraphs \
-header \
-filler N/A \
-names 12M 13M 23M 31M 48M 59M 64M 6M 7M 9M \
-i \
*M*10x.SNPcorr.bedgraph \
> male-union_10x.bedgraph

In [44]:
#Check output
!head male-union_10x.bedgraph
!wc -l male-union_10x.bedgraph

chrom	start	end	12M	13M	23M	31M	48M	59M	64M	6M	7M	9M
NC_007175.2	48	50	0.000000	0.000000	0.000000	3.125000	1.086957	0.000000	3.973510	0.653595	3.750000	1.754386
NC_007175.2	50	52	0.000000	0.000000	0.000000	1.470588	1.036269	0.000000	3.797468	0.632911	3.488372	1.666667
NC_007175.2	87	89	1.169591	1.293103	0.990099	0.671141	0.245700	0.000000	0.319489	0.666667	0.478469	0.000000
NC_007175.2	146	148	1.261830	0.461894	0.819672	0.332226	0.383142	0.000000	2.027027	0.702988	1.566580	0.456621
NC_007175.2	192	194	1.129944	1.271186	1.955990	0.303951	0.907029	0.476190	1.369863	0.161031	2.195122	0.840336
NC_007175.2	245	247	0.829876	0.550964	0.626959	1.321586	0.891530	1.986755	1.195219	0.451467	0.993377	0.609756
NC_007175.2	256	258	0.738007	0.496278	0.877193	0.404858	0.405954	1.111111	2.083333	0.202429	0.282486	1.117318
NC_007175.2	263	265	1.365188	0.917431	1.133144	0.000000	0.527704	1.058201	1.827243	0.193424	0.555556	0.537634
NC_007175.2	265	267	0.337838	0.453515	1.111111	0.763359	0.651890	1.595745

In [119]:
#Import union data into pandas
#Check head
df = pd.read_table("male-union_10x.bedgraph")
df.head(5)

chrom  start  end       12M       13M       23M       31M       48M  \
0  NC_007175.2     48   50  0.000000  0.000000  0.000000  3.125000  1.086957   
1  NC_007175.2     50   52  0.000000  0.000000  0.000000  1.470588  1.036269   
2  NC_007175.2     87   89  1.169591  1.293103  0.990099  0.671141  0.245700   
3  NC_007175.2    146  148  1.261830  0.461894  0.819672  0.332226  0.383142   
4  NC_007175.2    192  194  1.129944  1.271186  1.955990  0.303951  0.907029   

       59M       64M        6M        7M        9M  
0  0.00000  3.973510  0.653595  3.750000  1.754386  
1  0.00000  3.797468  0.632911  3.488372  1.666667  
2  0.00000  0.319489  0.666667  0.478469  0.000000  
3  0.00000  2.027027  0.702988  1.566580  0.456621  
4  0.47619  1.369863  0.161031  2.195122  0.840336

In [125]:
#Average all samples for total genome methylation information and save as a new column
#NA are not included in averages
#Check output
df['average'] = df[['12M', '13M', '23M', '31M', '48M', '59M', '64M', '6M', '7M', '9M']].mean(axis=1)
df.tail(10)

chrom     start       end  12M  13M  23M  31M  48M  59M  64M  \
11991486  NC_035789.1  32649654  32649656  0.0  0.0  NaN  NaN  0.0  0.0  NaN   
11991487  NC_035789.1  32649732  32649734  0.0  0.0  NaN  NaN  0.0  NaN  NaN   
11991488  NC_035789.1  32649736  32649738  0.0  0.0  NaN  NaN  0.0  NaN  NaN   
11991489  NC_035789.1  32649799  32649801  NaN  0.0  NaN  NaN  NaN  NaN  NaN   
11991490  NC_035789.1  32649876  32649878  0.0  0.0  NaN  NaN  NaN  0.0  NaN   
11991491  NC_035789.1  32649885  32649887  0.0  0.0  NaN  NaN  NaN  0.0  NaN   
11991492  NC_035789.1  32649895  32649897  0.0  0.0  NaN  NaN  NaN  0.0  NaN   
11991493  NC_035789.1  32649930  32649932  NaN  0.0  NaN  NaN  NaN  0.0  NaN   
11991494  NC_035789.1  32649933  32649935  NaN  0.0  NaN  NaN  NaN  0.0  0.0   
11991495  NC_035789.1  32649966  32649968  NaN  0.0  NaN  NaN  NaN  0.0  0.0   

           6M   7M  9M  total  average  
11991486  0.0  0.0 NaN    0.0      0.0  
11991487  0.0  0.0 NaN    0.0      0.0  
11991488  0.0  0.0 NaN    0.0      0.0  
11991489  NaN  NaN NaN    0.0      0.0  
11991490  0.0  0.0 NaN    0.0      0.0  
11991491  0.0  0.0 NaN    0.0      0.0  
11991492  0.0  0.0 NaN    0.0      0.0  
11991493  0.0  NaN NaN    0.0      0.0  
11991494  0.0  NaN NaN    0.0      0.0  
11991495  NaN  NaN NaN    0.0      0.0

In [126]:
#Save dataframe in a tabular format and include N/As. Do not include quotes.
df.to_csv("male-union-averages.bedgraph", sep = "\t", na_rep = "N/A", quoting = 3)

In [127]:
#Check pandas manipulations
!tail male-union-averages.bedgraph

11991486	NC_035789.1	32649654	32649656	0.0	0.0	N/A	N/A	0.0	0.0	N/A	0.0	0.0	N/A	0.0	0.0
11991487	NC_035789.1	32649732	32649734	0.0	0.0	N/A	N/A	0.0	N/A	N/A	0.0	0.0	N/A	0.0	0.0
11991488	NC_035789.1	32649736	32649738	0.0	0.0	N/A	N/A	0.0	N/A	N/A	0.0	0.0	N/A	0.0	0.0
11991489	NC_035789.1	32649799	32649801	N/A	0.0	N/A	N/A	N/A	N/A	N/A	N/A	N/A	N/A	0.0	0.0
11991490	NC_035789.1	32649876	32649878	0.0	0.0	N/A	N/A	N/A	0.0	N/A	0.0	0.0	N/A	0.0	0.0
11991491	NC_035789.1	32649885	32649887	0.0	0.0	N/A	N/A	N/A	0.0	N/A	0.0	0.0	N/A	0.0	0.0
11991492	NC_035789.1	32649895	32649897	0.0	0.0	N/A	N/A	N/A	0.0	N/A	0.0	0.0	N/A	0.0	0.0
11991493	NC_035789.1	32649930	32649932	N/A	0.0	N/A	N/A	N/A	0.0	N/A	0.0	N/A	N/A	0.0	0.0
11991494	NC_035789.1	32649933	32649935	N/A	0.0	N/A	N/A	N/A	0.0	0.0	0.0	N/A	N/A	0.0	0.0
11991495	NC_035789.1	32649966	32649968	N/A	0.0	N/A	N/A	N/A	0.0	0.0	N/A	N/A	N/A	0.0	0.0


In [128]:
#Print chr, start, end, and average columns
#Remove header
!awk '{print $2"\t"$3"\t"$4"\t"$15}' male-union-averages.bedgraph \
| tail -n +2 \
> male-union-averages_10x.SNPcorr.bedgraph

In [129]:
!head male-union-averages_10x.SNPcorr.bedgraph

NC_007175.2	48	50	1.4343447999999999
NC_007175.2	50	52	1.2092275000000001
NC_007175.2	87	89	0.5834259
NC_007175.2	146	148	0.801198
NC_007175.2	192	194	1.0610642000000001
NC_007175.2	245	247	0.9457489000000001
NC_007175.2	256	258	0.7718967
NC_007175.2	263	265	0.8115525000000001
NC_007175.2	265	267	0.7065609
NC_007175.2	331	333	0.8890879999999999


## 4. Characterize methylation for each CpG dinucleotude

I will use the following definitions:

- highly methylated: ≥ 50%
- moderately methylated: 10-50%
- lowly methylated : ≤ 10%

I will use the files with corrected SNP positions.

In [130]:
!find *10x.SNPcorr.bedgraph
!wc -l *10x.SNPcorr.bedgraph

12M_R1_val_1_10x.SNPcorr.bedgraph
13M_R1_val_1_10x.SNPcorr.bedgraph
16F_R1_val_1_10x.SNPcorr.bedgraph
19F_R1_val_1_10x.SNPcorr.bedgraph
22F_R1_val_1_10x.SNPcorr.bedgraph
23M_R1_val_1_10x.SNPcorr.bedgraph
29F_R1_val_1_10x.SNPcorr.bedgraph
31M_R1_val_1_10x.SNPcorr.bedgraph
35F_R1_val_1_10x.SNPcorr.bedgraph
36F_R1_val_1_10x.SNPcorr.bedgraph
39F_R1_val_1_10x.SNPcorr.bedgraph
3F_R1_val_1_10x.SNPcorr.bedgraph
41F_R1_val_1_10x.SNPcorr.bedgraph
44F_R1_val_1_10x.SNPcorr.bedgraph
48M_R1_val_1_10x.SNPcorr.bedgraph
50F_R1_val_1_10x.SNPcorr.bedgraph
52F_R1_val_1_10x.SNPcorr.bedgraph
53F_R1_val_1_10x.SNPcorr.bedgraph
54F_R1_val_1_10x.SNPcorr.bedgraph
59M_R1_val_1_10x.SNPcorr.bedgraph
64M_R1_val_1_10x.SNPcorr.bedgraph
6M_R1_val_1_10x.SNPcorr.bedgraph
76F_R1_val_1_10x.SNPcorr.bedgraph
77F_R1_val_1_10x.SNPcorr.bedgraph
7M_R1_val_1_10x.SNPcorr.bedgraph
9M_R1_val_1_10x.SNPcorr.bedgraph
fem-union-averages_10x.SNPcorr.bedgraph
male-union-averages_10x.SNPcorr.bedgraph
 8414935 12M_R1_val_1_10x.SNPcorr.bedgr

### 4a. Highly methylated loci

In [131]:
%%bash
for f in *10x.SNPcorr.bedgraph
do
    awk '{if ($4 >= 50) { print $1, $2, $3, $4 }}' ${f} \
    > ${f}-Meth
done

In [132]:
!head *-Meth

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth <==
NC_035780.1 100575 100577 93.750000
NC_035780.1 100634 100636 98.461538
NC_035780.1 100643 100645 98.571429
NC_035780.1 100651 100653 98.529412
NC_035780.1 100664 100666 98.484848
NC_035780.1 101083 101085 100.000000
NC_035780.1 101305 101307 95.121951
NC_035780.1 101408 101410 96.774194
NC_035780.1 101464 101466 94.871795
NC_035780.1 101594 101596 96.153846

==> 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth <==
NC_035780.1 22531 22533 56.250000
NC_035780.1 22536 22538 56.250000
NC_035780.1 75804 75806 58.823529
NC_035780.1 100558 100560 51.351351
NC_035780.1 100575 100577 96.551724
NC_035780.1 100634 100636 98.611111
NC_035780.1 100643 100645 95.000000
NC_035780.1 100651 100653 94.736842
NC_035780.1 100664 100666 95.945946
NC_035780.1 100974 100976 98.529412

==> 16F_R1_val_1_10x.SNPcorr.bedgraph-Meth <==
NC_035780.1 100575 100577 100.000000
NC_035780.1 100634 100636 91.525424
NC_035780.1 100643 100645 80.303030
NC_035780.1 100651 100653 93.7500

In [133]:
!wc -l *-Meth

 1172075 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth
 1166184 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth
  989685 16F_R1_val_1_10x.SNPcorr.bedgraph-Meth
  998280 19F_R1_val_1_10x.SNPcorr.bedgraph-Meth
  925525 22F_R1_val_1_10x.SNPcorr.bedgraph-Meth
 1207749 23M_R1_val_1_10x.SNPcorr.bedgraph-Meth
  928713 29F_R1_val_1_10x.SNPcorr.bedgraph-Meth
 1119351 31M_R1_val_1_10x.SNPcorr.bedgraph-Meth
  997234 35F_R1_val_1_10x.SNPcorr.bedgraph-Meth
  995424 36F_R1_val_1_10x.SNPcorr.bedgraph-Meth
  972293 39F_R1_val_1_10x.SNPcorr.bedgraph-Meth
  970953 3F_R1_val_1_10x.SNPcorr.bedgraph-Meth
  825342 41F_R1_val_1_10x.SNPcorr.bedgraph-Meth
 1036681 44F_R1_val_1_10x.SNPcorr.bedgraph-Meth
 1099961 48M_R1_val_1_10x.SNPcorr.bedgraph-Meth
  964824 50F_R1_val_1_10x.SNPcorr.bedgraph-Meth
  972492 52F_R1_val_1_10x.SNPcorr.bedgraph-Meth
  999871 53F_R1_val_1_10x.SNPcorr.bedgraph-Meth
 1007868 54F_R1_val_1_10x.SNPcorr.bedgraph-Meth
 1034559 59M_R1_val_1_10x.SNPcorr.bedgraph-Meth
 1123237 64M_R1_val_1_10x.SNPcorr.bedgrap

In [134]:
#Get line counts for each fine
# Remove 10th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-Meth \
| sed '29,$ d' \
| awk '{print $1"\t"$2}' \
> Meth-counts.txt

In [135]:
!tail Meth-counts.txt

1007868	54F_R1_val_1_10x.SNPcorr.bedgraph-Meth
1034559	59M_R1_val_1_10x.SNPcorr.bedgraph-Meth
1123237	64M_R1_val_1_10x.SNPcorr.bedgraph-Meth
1050757	6M_R1_val_1_10x.SNPcorr.bedgraph-Meth
998920	76F_R1_val_1_10x.SNPcorr.bedgraph-Meth
983080	77F_R1_val_1_10x.SNPcorr.bedgraph-Meth
1136818	7M_R1_val_1_10x.SNPcorr.bedgraph-Meth
1065292	9M_R1_val_1_10x.SNPcorr.bedgraph-Meth
1254583	fem-union-averages_10x.SNPcorr.bedgraph-Meth
1467485	male-union-averages_10x.SNPcorr.bedgraph-Meth


### 4b. Moderately methylated loci

In [136]:
%%bash
for f in *10x.SNPcorr.bedgraph
do
    awk '{if ($4 < 50) { print $1, $2, $3, $4}}' ${f} \
    | awk '{if ($4 > 10) { print $1, $2, $3, $4 }}' \
    > ${f}-modMeth
done

In [137]:
!head *-modMeth

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth <==
NC_035780.1 11418 11420 12.500000
NC_035780.1 11437 11439 15.789474
NC_035780.1 11446 11448 16.666667
NC_035780.1 11465 11467 20.000000
NC_035780.1 14430 14432 27.272727
NC_035780.1 14453 14455 14.285714
NC_035780.1 16113 16115 45.454545
NC_035780.1 16307 16309 14.285714
NC_035780.1 16817 16819 15.000000
NC_035780.1 21767 21769 10.526316

==> 13M_R1_val_1_10x.SNPcorr.bedgraph-modMeth <==
NC_035780.1 9266 9268 12.121212
NC_035780.1 14430 14432 15.384615
NC_035780.1 14453 14455 15.384615
NC_035780.1 19741 19743 17.567568
NC_035780.1 19960 19962 17.000000
NC_035780.1 20026 20028 11.666667
NC_035780.1 20044 20046 10.526316
NC_035780.1 20081 20083 10.416667
NC_035780.1 22529 22531 43.750000
NC_035780.1 23584 23586 23.076923

==> 16F_R1_val_1_10x.SNPcorr.bedgraph-modMeth <==
NC_035780.1 12757 12759 41.666667
NC_035780.1 12796 12798 27.272727
NC_035780.1 12835 12837 20.000000
NC_035780.1 14430 14432 18.750000
NC_035780.1 14453 14455 18.750000


In [138]:
!wc -l *-modMeth

  469413 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  468971 13M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  628398 16F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  640938 19F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  589664 22F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  481345 23M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  607814 29F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  372895 31M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  599484 35F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  610781 36F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  589170 39F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  587527 3F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  550976 41F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  816442 44F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  430914 48M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  636465 50F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  650263 52F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  629421 53F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  638438 54F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
  353563 59M_R1_val_1_10x.SNPcor

In [139]:
#Get line counts for each fine
# Remove 29th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-modMeth \
| sed '29,$ d' \
| awk '{print $1"\t"$2}' \
> modMeth-counts.txt

In [140]:
!tail modMeth-counts.txt

638438	54F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
353563	59M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
425919	64M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
397826	6M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
566946	76F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
600153	77F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
407720	7M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
383314	9M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
1211567	fem-union-averages_10x.SNPcorr.bedgraph-modMeth
866734	male-union-averages_10x.SNPcorr.bedgraph-modMeth


### 4c. Lowly methylated loci

In [141]:
%%bash
for f in *10x.SNPcorr.bedgraph
do
    awk '{if ($4 <= 10) { print $1, $2, $3, $4 }}' ${f} \
    > ${f}-lowMeth
done

In [142]:
!head *-lowMeth

==> 10x.SNPcorr.bedgraph-lowMeth <==

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth <==
NC_007175.2 48 50 0.000000
NC_007175.2 50 52 0.000000
NC_007175.2 87 89 1.169591
NC_007175.2 146 148 1.261830
NC_007175.2 192 194 1.129944
NC_007175.2 245 247 0.829876
NC_007175.2 256 258 0.738007
NC_007175.2 263 265 1.365188
NC_007175.2 265 267 0.337838
NC_007175.2 331 333 0.645161

==> 13M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth <==
NC_007175.2 48 50 0.000000
NC_007175.2 50 52 0.000000
NC_007175.2 87 89 1.293103
NC_007175.2 146 148 0.461894
NC_007175.2 192 194 1.271186
NC_007175.2 245 247 0.550964
NC_007175.2 256 258 0.496278
NC_007175.2 263 265 0.917431
NC_007175.2 265 267 0.453515
NC_007175.2 331 333 0.826446

==> 16F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth <==
NC_007175.2 48 50 1.923077
NC_007175.2 50 52 1.626016
NC_007175.2 87 89 1.045857
NC_007175.2 146 148 1.502146
NC_007175.2 192 194 1.726908
NC_007175.2 245 247 1.228250
NC_007175.2 256 258 1.417467
NC_007175.2 263 265 1.681034
NC_007175.2 265 


==> fem-union-averages_10x.SNPcorr.bedgraph-lowMeth <==
NC_007175.2 48 50 1.4164250624999999
NC_007175.2 50 52 1.3472570625
NC_007175.2 87 89 0.813770375
NC_007175.2 146 148 1.1229276875
NC_007175.2 192 194 1.19816225
NC_007175.2 245 247 0.9728829374999999
NC_007175.2 256 258 1.0959236250000002
NC_007175.2 263 265 1.0578576875
NC_007175.2 265 267 1.0646793125
NC_007175.2 331 333 1.1050068124999999

==> male-union-averages_10x.SNPcorr.bedgraph-lowMeth <==
NC_007175.2 48 50 1.4343447999999999
NC_007175.2 50 52 1.2092275000000001
NC_007175.2 87 89 0.5834259
NC_007175.2 146 148 0.801198
NC_007175.2 192 194 1.0610642000000001
NC_007175.2 245 247 0.9457489000000001
NC_007175.2 256 258 0.7718967
NC_007175.2 263 265 0.8115525000000001
NC_007175.2 265 267 0.7065609
NC_007175.2 331 333 0.8890879999999999


In [147]:
!wc -l *-lowMeth

 6773447 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6795754 13M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6657213 16F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6678673 19F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6105344 22F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6864672 23M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6412017 29F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6266637 31M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6504469 35F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6584940 36F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6375032 39F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6772748 3F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 5471284 41F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 7538432 44F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6377489 48M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6516209 50F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6753644 52F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6684138 53F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 6750931 54F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
 5687100 59M_R1_val_1_10x.SNPcor

In [148]:
#Get line counts for each fine
# Remove 10th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-lowMeth \
| sed '29,$ d' \
| awk '{print $1"\t"$2}' \
> lowMeth-counts.txt

In [150]:
!tail lowMeth-counts.txt

6750931	54F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
5687100	59M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
6552060	64M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
5962227	6M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
6414015	76F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
6631520	77F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
6329791	7M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
6221322	9M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
10212421	fem-union-averages_10x.SNPcorr.bedgraph-lowMeth
9657277	male-union-averages_10x.SNPcorr.bedgraph-lowMeth


## 5. Characterize genomic location of CpGs

I will identify overlaps between CpG loci (methylated, sparsely methylated, unmethylated) and various genome feature tracks:

- gene
- exon UTR
- CDS
- intron
- upstream flanks
- downstream flanks
- intergenic regions
- lncRNA
- transposable elements

Since the exon track = exon UTR + CDS, and mRNA = exon + intron, I will not need to use those tracks separately.

In [6]:
#28 file types (26 samples + 2 unions), 3 files per type (Meth, modMeth, lowMeth) = 84 total
!find *10x.SNPcorr.bedgraph-*
!find *10x.SNPcorr.bedgraph-* | wc -l

12M_R1_val_1_10x.SNPcorr.bedgraph-Meth
12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
13M_R1_val_1_10x.SNPcorr.bedgraph-Meth
13M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
13M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
16F_R1_val_1_10x.SNPcorr.bedgraph-Meth
16F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
16F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
19F_R1_val_1_10x.SNPcorr.bedgraph-Meth
19F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
19F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
22F_R1_val_1_10x.SNPcorr.bedgraph-Meth
22F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
22F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
23M_R1_val_1_10x.SNPcorr.bedgraph-Meth
23M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
23M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
29F_R1_val_1_10x.SNPcorr.bedgraph-Meth
29F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
29F_R1_val_1_10x.SNPcorr.bedgraph-modMeth
31M_R1_val_1_10x.SNPcorr.bedgraph-Meth
31M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth
31M_R1_val_1_10x.SNPcorr.bedgraph-modMeth
35F_R1_val_1_10x

In [7]:
%%bash

for f in *10x.SNPcorr.bedgraph-*
do
    awk '{print $1"\t"$2"\t"$3}' ${f} > ${f}.bed
    wc -l ${f}.bed
done

 1172075 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed
 6773447 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed
  469413 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed
 1166184 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed
 6795754 13M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed
  468971 13M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed
  989685 16F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed
 6657213 16F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed
  628398 16F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed
  998280 19F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed
 6678673 19F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed
  640938 19F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed
  925525 22F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed
 6105344 22F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed
  589664 22F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed
 1207749 23M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed
 6864672 23M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed
  481345 23M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed
  928713 29F_R1_val_1_10x.SN

In [10]:
!find *bed | wc -l

      84


### 4b. Gene

#### Overlaps between CpG background and genes for downstream annotation

In [11]:
#Female samples

!{bedtoolsDirectory}intersectBed \
-wb \
-a fem-union-averages_10x.SNPcorr.bedgraph \
-b ../../genome-features/C_virginica-3.0-gene.gff \
> fem-union-averages_10x-wb.bed
!head fem-union-averages_10x-wb.bed
!wc -l fem-union-averages_10x-wb.bed

NC_007175.2	48	50	1.4164250624999999	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_007175.2	50	52	1.3472570625	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_007175.2	87	89	0.813770375	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_007175.2	146	148	1.1229276875	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_007175.2	192	194	1.19816225	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_007175.2	245	247	0.9728829374999999	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_007175.2	2

In [12]:
#Male samples

!{bedtoolsDirectory}intersectBed \
-wb \
-a male-union-averages_10x.SNPcorr.bedgraph \
-b ../../genome-features/C_virginica-3.0-gene.gff \
> male-union-averages_10x-wb.bed
!head male-union-averages_10x-wb.bed
!wc -l male-union-averages_10x-wb.bed

NC_007175.2	48	50	1.4343447999999999	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_007175.2	50	52	1.2092275000000001	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_007175.2	87	89	0.5834259	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_007175.2	146	148	0.801198	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_007175.2	192	194	1.0610642000000001	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_007175.2	245	247	0.9457489000000001	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_00

#### Overlaps without annotations

In [13]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-features/C_virginica-3.0-gene.gff \
    > ${f}-Gene
done

In [14]:
#Check output
!head *Gene

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-Gene <==
NC_035780.1	100575	100577
NC_035780.1	100634	100636
NC_035780.1	100643	100645
NC_035780.1	100651	100653
NC_035780.1	100664	100666
NC_035780.1	101083	101085
NC_035780.1	101305	101307
NC_035780.1	101408	101410
NC_035780.1	101464	101466
NC_035780.1	101594	101596

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-Gene <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_007175.2	87	89
NC_007175.2	146	148
NC_007175.2	192	194
NC_007175.2	245	247
NC_007175.2	256	258
NC_007175.2	263	265
NC_007175.2	265	267
NC_007175.2	331	333

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-Gene <==
NC_035780.1	14430	14432
NC_035780.1	14453	14455
NC_035780.1	94598	94600
NC_035780.1	100974	100976
NC_035780.1	102024	102026
NC_035780.1	102122	102124
NC_035780.1	102915	102917
NC_035780.1	103192	103194
NC_035780.1	103198	103200
NC_035780.1	103268	103270

==> 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-Gene <==
NC_035780.1	100558	100560
NC_035780.1	100575	100577
NC_0357


==> 36F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-Gene <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_007175.2	87	89
NC_007175.2	146	148
NC_007175.2	192	194
NC_007175.2	245	247
NC_007175.2	256	258
NC_007175.2	263	265
NC_007175.2	265	267
NC_007175.2	331	333

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-Gene <==
NC_035780.1	14430	14432
NC_035780.1	101305	101307
NC_035780.1	101464	101466
NC_035780.1	103480	103482
NC_035780.1	106083	106085
NC_035780.1	165053	165055
NC_035780.1	165094	165096
NC_035780.1	165148	165150
NC_035780.1	165161	165163
NC_035780.1	165180	165182

==> 39F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-Gene <==
NC_035780.1	100575	100577
NC_035780.1	100634	100636
NC_035780.1	100643	100645
NC_035780.1	100651	100653
NC_035780.1	100664	100666
NC_035780.1	100916	100918
NC_035780.1	100974	100976
NC_035780.1	101083	101085
NC_035780.1	101305	101307
NC_035780.1	101408	101410

==> 39F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-Gene <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_007175.2	87	


==> 54F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-Gene <==
NC_035780.1	13597	13599
NC_035780.1	13651	13653
NC_035780.1	13725	13727
NC_035780.1	52587	52589
NC_035780.1	100916	100918
NC_035780.1	101408	101410
NC_035780.1	101464	101466
NC_035780.1	102122	102124
NC_035780.1	103192	103194
NC_035780.1	103198	103200

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-Gene <==
NC_035780.1	100558	100560
NC_035780.1	100575	100577
NC_035780.1	100643	100645
NC_035780.1	100651	100653
NC_035780.1	100664	100666
NC_035780.1	100974	100976
NC_035780.1	101083	101085
NC_035780.1	101305	101307
NC_035780.1	101464	101466
NC_035780.1	101594	101596

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-Gene <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_007175.2	87	89
NC_007175.2	146	148
NC_007175.2	192	194
NC_007175.2	245	247
NC_007175.2	256	258
NC_007175.2	263	265
NC_007175.2	265	267
NC_007175.2	331	333

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-Gene <==
NC_035780.1	88054	88056
NC_035780.1	88056	88058
NC_035780


==> fem-union-averages_10x.SNPcorr.bedgraph-lowMeth.bed-Gene <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_007175.2	87	89
NC_007175.2	146	148
NC_007175.2	192	194
NC_007175.2	245	247
NC_007175.2	256	258
NC_007175.2	263	265
NC_007175.2	265	267
NC_007175.2	331	333

==> fem-union-averages_10x.SNPcorr.bedgraph-modMeth.bed-Gene <==
NC_035780.1	14144	14146
NC_035780.1	14430	14432
NC_035780.1	14453	14455
NC_035780.1	100558	100560
NC_035780.1	100581	100583
NC_035780.1	100916	100918
NC_035780.1	100974	100976
NC_035780.1	101464	101466
NC_035780.1	102024	102026
NC_035780.1	102122	102124

==> male-union-averages_10x-wb.bed-Gene <==
NC_007175.2	48	50	1.4343447999999999	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_007175.2	50	52	1.2092275000000001	NC_007175.2	RefSeq	gene	1	1623	.	+	.	ID=gene-COX1;Dbxref=GeneID:3453225;Name=COX1;gbkey=Gene;gene=COX1;gene_biotype=protein_coding
NC_007175.2	87	89	0.5834259	NC_007175.2

In [15]:
#Count number of overlaps
!wc -l *Gene

 1044969 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-Gene
 3425214 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-Gene
  289008 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-Gene
 1041888 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-Gene
 3454085 13M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-Gene
  284611 13M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-Gene
  882752 16F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-Gene
 3367087 16F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-Gene
  431518 16F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-Gene
  889680 19F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-Gene
 3384429 19F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-Gene
  441374 19F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-Gene
  830466 22F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-Gene
 3117208 22F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-Gene
  420782 22F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-Gene
 1072830 23M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-Gene
 3458303 23M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-Gen

In [22]:
#Get line counts for each fine
# Remove 87th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-Gene \
| sed '87,$ d' \
| awk '{print $1"\t"$2}' \
> Gene-counts.txt

### 4c. CDS

In [24]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-features/C_virginica-3.0-CDS.gff \
    > ${f}-CDS
done

In [25]:
#Check output
!head *CDS

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-CDS <==
NC_035780.1	100575	100577
NC_035780.1	100634	100636
NC_035780.1	100643	100645
NC_035780.1	100651	100653
NC_035780.1	105574	105576
NC_035780.1	105580	105582
NC_035780.1	106083	106085
NC_035780.1	258993	258995
NC_035780.1	259012	259014
NC_035780.1	259032	259034

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-CDS <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_007175.2	87	89
NC_007175.2	146	148
NC_007175.2	192	194
NC_007175.2	245	247
NC_007175.2	256	258
NC_007175.2	263	265
NC_007175.2	265	267
NC_007175.2	331	333

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-CDS <==
NC_035780.1	94598	94600
NC_035780.1	157508	157510
NC_035780.1	250321	250323
NC_035780.1	250344	250346
NC_035780.1	250348	250350
NC_035780.1	250387	250389
NC_035780.1	250394	250396
NC_035780.1	250416	250418
NC_035780.1	250425	250427
NC_035780.1	250448	250450

==> 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-CDS <==
NC_035780.1	100558	100560
NC_035780.1	100575	100577
NC_0357

NC_035780.1	246144	246146

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-CDS <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_007175.2	87	89
NC_007175.2	146	148
NC_007175.2	192	194
NC_007175.2	245	247
NC_007175.2	256	258
NC_007175.2	263	265
NC_007175.2	265	267
NC_007175.2	331	333

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-CDS <==
NC_035780.1	106083	106085
NC_035780.1	166180	166182
NC_035780.1	166192	166194
NC_035780.1	166249	166251
NC_035780.1	166290	166292
NC_035780.1	166351	166353
NC_035780.1	246023	246025
NC_035780.1	246047	246049
NC_035780.1	246108	246110
NC_035780.1	246197	246199

==> 39F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-CDS <==
NC_035780.1	100575	100577
NC_035780.1	100634	100636
NC_035780.1	100643	100645
NC_035780.1	100651	100653
NC_035780.1	105574	105576
NC_035780.1	250416	250418
NC_035780.1	250425	250427
NC_035780.1	250453	250455
NC_035780.1	258993	258995
NC_035780.1	259012	259014

==> 39F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-CDS <==
NC_007175.2	48	50
NC_007175


==> 54F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-CDS <==
NC_035780.1	106083	106085
NC_035780.1	258993	258995
NC_035780.1	259236	259238
NC_035780.1	259354	259356
NC_035780.1	261803	261805
NC_035780.1	261815	261817
NC_035780.1	262054	262056
NC_035780.1	262057	262059
NC_035780.1	262135	262137
NC_035780.1	265027	265029

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-CDS <==
NC_035780.1	100558	100560
NC_035780.1	100575	100577
NC_035780.1	100643	100645
NC_035780.1	100651	100653
NC_035780.1	105574	105576
NC_035780.1	250387	250389
NC_035780.1	250394	250396
NC_035780.1	250416	250418
NC_035780.1	250425	250427
NC_035780.1	250448	250450

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-CDS <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_007175.2	87	89
NC_007175.2	146	148
NC_007175.2	192	194
NC_007175.2	245	247
NC_007175.2	256	258
NC_007175.2	263	265
NC_007175.2	265	267
NC_007175.2	331	333

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-CDS <==
NC_035780.1	100634	100636
NC_035780.1	105580	105582
N


==> fem-union-averages_10x.SNPcorr.bedgraph-Meth.bed-CDS <==
NC_035780.1	100575	100577
NC_035780.1	100634	100636
NC_035780.1	100643	100645
NC_035780.1	100651	100653
NC_035780.1	105574	105576
NC_035780.1	105580	105582
NC_035780.1	250321	250323
NC_035780.1	250344	250346
NC_035780.1	250348	250350
NC_035780.1	250387	250389

==> fem-union-averages_10x.SNPcorr.bedgraph-lowMeth.bed-CDS <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_007175.2	87	89
NC_007175.2	146	148
NC_007175.2	192	194
NC_007175.2	245	247
NC_007175.2	256	258
NC_007175.2	263	265
NC_007175.2	265	267
NC_007175.2	331	333

==> fem-union-averages_10x.SNPcorr.bedgraph-modMeth.bed-CDS <==
NC_035780.1	100558	100560
NC_035780.1	100581	100583
NC_035780.1	106083	106085
NC_035780.1	165853	165855
NC_035780.1	245773	245775
NC_035780.1	246023	246025
NC_035780.1	246047	246049
NC_035780.1	246063	246065
NC_035780.1	246108	246110
NC_035780.1	246144	246146

==> male-union-averages_10x-wb.bed-CDS <==
NC_007175.2	48	50	1.4343447999999999	NC_007175.2	R

In [26]:
#Count number of overlaps
!wc -l *CDS

  371121 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-CDS
  834671 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-CDS
   44126 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-CDS
  372065 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-CDS
  849637 13M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-CDS
   42459 13M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-CDS
  344324 16F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-CDS
  810820 16F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-CDS
   68328 16F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-CDS
  344962 19F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-CDS
  821826 19F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-CDS
   68642 19F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-CDS
  323489 22F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-CDS
  766441 22F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-CDS
   68418 22F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-CDS
  377045 23M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-CDS
  844472 23M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-CDS
   43719 23M_R1

In [27]:
#Get line counts for each fine
# Remove 87th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-CDS \
| sed '87,$ d' \
| awk '{print $1"\t"$2}' \
> CDS-counts.txt

### 4d. Exon UTR

In [28]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-features/C_virginica-3.0-exonUTR.gff \
    > ${f}-exonUTR
done

In [29]:
#Check output
!head *exonUTR

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-exonUTR <==
NC_035780.1	106235	106237
NC_035780.1	106305	106307
NC_035780.1	258267	258269
NC_035780.1	258278	258280
NC_035780.1	258302	258304
NC_035780.1	258320	258322
NC_035780.1	258324	258326
NC_035780.1	258347	258349
NC_035780.1	258383	258385
NC_035780.1	258511	258513

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-exonUTR <==
NC_007175.2	1749	1751
NC_007175.2	1766	1768
NC_007175.2	1825	1827
NC_007175.2	1836	1838
NC_007175.2	1842	1844
NC_007175.2	1846	1848
NC_007175.2	1854	1856
NC_007175.2	1873	1875
NC_007175.2	1918	1920
NC_007175.2	2003	2005

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-exonUTR <==
NC_035780.1	264434	264436
NC_035780.1	293573	293575
NC_035780.1	293657	293659
NC_035780.1	293667	293669
NC_035780.1	293726	293728
NC_035780.1	309825	309827
NC_035780.1	370586	370588
NC_035780.1	380582	380584
NC_035780.1	380653	380655
NC_035780.1	380695	380697

==> 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-exonUTR <==
NC_035780.1	106


==> 36F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-exonUTR <==
NC_035780.1	258302	258304
NC_035780.1	258320	258322
NC_035780.1	258324	258326
NC_035780.1	258347	258349
NC_035780.1	258383	258385
NC_035780.1	258511	258513
NC_035780.1	258605	258607
NC_035780.1	258622	258624
NC_035780.1	258914	258916
NC_035780.1	258924	258926

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-exonUTR <==
NC_007175.2	1749	1751
NC_007175.2	1766	1768
NC_007175.2	1825	1827
NC_007175.2	1836	1838
NC_007175.2	1842	1844
NC_007175.2	1846	1848
NC_007175.2	1854	1856
NC_007175.2	1873	1875
NC_007175.2	1918	1920
NC_007175.2	2003	2005

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-exonUTR <==
NC_035780.1	165709	165711
NC_035780.1	165727	165729
NC_035780.1	245716	245718
NC_035780.1	245725	245727
NC_035780.1	258267	258269
NC_035780.1	258269	258271
NC_035780.1	258278	258280
NC_035780.1	258744	258746
NC_035780.1	264326	264328
NC_035780.1	264434	264436

==> 39F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-exonUTR <==
NC_035780.1	25


==> 54F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-exonUTR <==
NC_035780.1	258267	258269
NC_035780.1	258278	258280
NC_035780.1	258302	258304
NC_035780.1	258320	258322
NC_035780.1	258324	258326
NC_035780.1	258622	258624
NC_035780.1	258914	258916
NC_035780.1	258934	258936
NC_035780.1	258943	258945
NC_035780.1	261610	261612

==> 54F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-exonUTR <==
NC_007175.2	1749	1751
NC_007175.2	1766	1768
NC_007175.2	1825	1827
NC_007175.2	1836	1838
NC_007175.2	1842	1844
NC_007175.2	1846	1848
NC_007175.2	1854	1856
NC_007175.2	1873	1875
NC_007175.2	1918	1920
NC_007175.2	2003	2005

==> 54F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-exonUTR <==
NC_035780.1	13597	13599
NC_035780.1	106305	106307
NC_035780.1	240133	240135
NC_035780.1	258347	258349
NC_035780.1	258383	258385
NC_035780.1	258511	258513
NC_035780.1	258744	258746
NC_035780.1	263684	263686
NC_035780.1	263928	263930
NC_035780.1	263974	263976

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-exonUTR <==
NC_035780.1	2582


==> fem-union-averages_10x.SNPcorr.bedgraph-Meth.bed-exonUTR <==
NC_035780.1	258267	258269
NC_035780.1	258278	258280
NC_035780.1	258302	258304
NC_035780.1	258320	258322
NC_035780.1	258324	258326
NC_035780.1	258347	258349
NC_035780.1	258383	258385
NC_035780.1	258511	258513
NC_035780.1	258605	258607
NC_035780.1	258622	258624

==> fem-union-averages_10x.SNPcorr.bedgraph-lowMeth.bed-exonUTR <==
NC_007175.2	1749	1751
NC_007175.2	1766	1768
NC_007175.2	1825	1827
NC_007175.2	1836	1838
NC_007175.2	1842	1844
NC_007175.2	1846	1848
NC_007175.2	1854	1856
NC_007175.2	1873	1875
NC_007175.2	1918	1920
NC_007175.2	2003	2005

==> fem-union-averages_10x.SNPcorr.bedgraph-modMeth.bed-exonUTR <==
NC_035780.1	106235	106237
NC_035780.1	106305	106307
NC_035780.1	240133	240135
NC_035780.1	245716	245718
NC_035780.1	258269	258271
NC_035780.1	258380	258382
NC_035780.1	258471	258473
NC_035780.1	263928	263930
NC_035780.1	264434	264436
NC_035780.1	293726	293728

==> male-union-averages_10x-wb.bed-exonUTR <==
NC_03578

In [30]:
#Count number of overlaps
!wc -l *exonUTR

   63828 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-exonUTR
  330778 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-exonUTR
   17577 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-exonUTR
   62845 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-exonUTR
  331930 13M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-exonUTR
   16707 13M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-exonUTR
   51503 16F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-exonUTR
  328301 16F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-exonUTR
   27354 16F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-exonUTR
   52566 19F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-exonUTR
  327570 19F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-exonUTR
   27587 19F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-exonUTR
   48268 22F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-exonUTR
  310187 22F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-exonUTR
   29104 22F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-exonUTR
   66732 23M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-exonUTR
  332144 2

In [31]:
#Get line counts for each fine
# Remove 87th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-exonUTR \
| sed '87,$ d' \
| awk '{print $1"\t"$2}' \
> exonUTR-counts.txt

### 4e. Intron

In [32]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-features/C_virginica-3.0-intron.bed \
    > ${f}-intron
done

In [33]:
#Check output
!head *intron

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intron <==
NC_035780.1	100664	100666
NC_035780.1	101083	101085
NC_035780.1	101305	101307
NC_035780.1	101408	101410
NC_035780.1	101464	101466
NC_035780.1	101594	101596
NC_035780.1	101628	101630
NC_035780.1	101655	101657
NC_035780.1	101852	101854
NC_035780.1	101922	101924

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intron <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_007175.2	87	89
NC_007175.2	146	148
NC_007175.2	192	194
NC_007175.2	245	247
NC_007175.2	256	258
NC_007175.2	263	265
NC_007175.2	265	267
NC_007175.2	331	333

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intron <==
NC_035780.1	14430	14432
NC_035780.1	14453	14455
NC_035780.1	100974	100976
NC_035780.1	102024	102026
NC_035780.1	102122	102124
NC_035780.1	102915	102917
NC_035780.1	103192	103194
NC_035780.1	103198	103200
NC_035780.1	103268	103270
NC_035780.1	103272	103274

==> 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intron <==
NC_035780.1	100664	100666
NC_035780.1	100974	1009


==> 36F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intron <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_007175.2	87	89
NC_007175.2	146	148
NC_007175.2	192	194
NC_007175.2	245	247
NC_007175.2	256	258
NC_007175.2	263	265
NC_007175.2	265	267
NC_007175.2	331	333

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intron <==
NC_035780.1	14430	14432
NC_035780.1	101305	101307
NC_035780.1	101464	101466
NC_035780.1	103480	103482
NC_035780.1	165053	165055
NC_035780.1	165094	165096
NC_035780.1	165148	165150
NC_035780.1	165161	165163
NC_035780.1	165180	165182
NC_035780.1	165296	165298

==> 39F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intron <==
NC_035780.1	100664	100666
NC_035780.1	100916	100918
NC_035780.1	100974	100976
NC_035780.1	101083	101085
NC_035780.1	101305	101307
NC_035780.1	101408	101410
NC_035780.1	101464	101466
NC_035780.1	101594	101596
NC_035780.1	101628	101630
NC_035780.1	101655	101657

==> 39F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intron <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_0071


==> 54F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intron <==
NC_035780.1	13651	13653
NC_035780.1	13725	13727
NC_035780.1	52587	52589
NC_035780.1	100916	100918
NC_035780.1	101408	101410
NC_035780.1	101464	101466
NC_035780.1	102122	102124
NC_035780.1	103192	103194
NC_035780.1	103198	103200
NC_035780.1	105649	105651

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intron <==
NC_035780.1	100664	100666
NC_035780.1	100974	100976
NC_035780.1	101083	101085
NC_035780.1	101305	101307
NC_035780.1	101464	101466
NC_035780.1	101594	101596
NC_035780.1	101628	101630
NC_035780.1	101655	101657
NC_035780.1	101852	101854
NC_035780.1	101922	101924

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intron <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_007175.2	87	89
NC_007175.2	146	148
NC_007175.2	192	194
NC_007175.2	245	247
NC_007175.2	256	258
NC_007175.2	263	265
NC_007175.2	265	267
NC_007175.2	331	333

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intron <==
NC_035780.1	88054	88056
NC_035780.1	88056	88058


==> fem-union-averages_10x.SNPcorr.bedgraph-Meth.bed-intron <==
NC_035780.1	100664	100666
NC_035780.1	101083	101085
NC_035780.1	101305	101307
NC_035780.1	101408	101410
NC_035780.1	101594	101596
NC_035780.1	101628	101630
NC_035780.1	101655	101657
NC_035780.1	101852	101854
NC_035780.1	101922	101924
NC_035780.1	102411	102413

==> fem-union-averages_10x.SNPcorr.bedgraph-lowMeth.bed-intron <==
NC_007175.2	48	50
NC_007175.2	50	52
NC_007175.2	87	89
NC_007175.2	146	148
NC_007175.2	192	194
NC_007175.2	245	247
NC_007175.2	256	258
NC_007175.2	263	265
NC_007175.2	265	267
NC_007175.2	331	333

==> fem-union-averages_10x.SNPcorr.bedgraph-modMeth.bed-intron <==
NC_035780.1	14144	14146
NC_035780.1	14430	14432
NC_035780.1	14453	14455
NC_035780.1	100916	100918
NC_035780.1	100974	100976
NC_035780.1	101464	101466
NC_035780.1	102024	102026
NC_035780.1	102122	102124
NC_035780.1	102592	102594
NC_035780.1	102656	102658

==> male-union-averages_10x-wb.bed-intron <==
NC_007175.2	48	50	1.4343447999999999	NC_0071

In [34]:
#Count number of overlaps
!wc -l *intron

  618079 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intron
 2289548 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intron
  228948 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intron
  615152 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intron
 2302263 13M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intron
  227439 13M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intron
  494050 16F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intron
 2257565 16F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intron
  338172 16F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intron
  499445 19F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intron
 2264618 19F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intron
  347271 19F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intron
  465612 22F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intron
 2068474 22F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intron
  325591 22F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intron
  637354 23M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intron
 2311820 23M_R1_val_1_10x.

In [35]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-intron \
| sed '87,$ d' \
| awk '{print $1"\t"$2}' \
> intron-counts.txt

### 4f. Upstream flanks

In [36]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-features/C_virginica-3.0-upstream.gff \
    > ${f}-upstreamFlanks
done

In [37]:
#Check output
!head *upstreamFlanks

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-upstreamFlanks <==
NC_035780.1	314599	314601
NC_035780.1	314635	314637
NC_035780.1	314783	314785
NC_035780.1	314940	314942
NC_035780.1	314950	314952
NC_035780.1	314963	314965
NC_035780.1	314981	314983
NC_035780.1	314984	314986
NC_035780.1	315000	315002
NC_035780.1	585861	585863

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-upstreamFlanks <==
NC_007175.2	1658	1660
NC_007175.2	1749	1751
NC_007175.2	1766	1768
NC_007175.2	1825	1827
NC_007175.2	1836	1838
NC_007175.2	1842	1844
NC_007175.2	1846	1848
NC_007175.2	1854	1856
NC_007175.2	1873	1875
NC_007175.2	1918	1920

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-upstreamFlanks <==
NC_035780.1	585894	585896
NC_035780.1	585904	585906
NC_035780.1	586007	586009
NC_035780.1	586275	586277
NC_035780.1	586293	586295
NC_035780.1	586315	586317
NC_035780.1	586329	586331
NC_035780.1	586332	586334
NC_035780.1	586359	586361
NC_035780.1	662903	662905

==> 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-upstre


==> 36F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-upstreamFlanks <==
NC_035780.1	253243	253245
NC_035780.1	253259	253261
NC_035780.1	253261	253263
NC_035780.1	253334	253336
NC_035780.1	253351	253353
NC_035780.1	253384	253386
NC_035780.1	253444	253446
NC_035780.1	253694	253696
NC_035780.1	253826	253828
NC_035780.1	253832	253834

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-upstreamFlanks <==
NC_007175.2	1658	1660
NC_007175.2	1749	1751
NC_007175.2	1766	1768
NC_007175.2	1825	1827
NC_007175.2	1836	1838
NC_007175.2	1842	1844
NC_007175.2	1846	1848
NC_007175.2	1854	1856
NC_007175.2	1873	1875
NC_007175.2	1918	1920

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-upstreamFlanks <==
NC_035780.1	12633	12635
NC_035780.1	12685	12687
NC_035780.1	12757	12759
NC_035780.1	12796	12798
NC_035780.1	99371	99373
NC_035780.1	99376	99378
NC_035780.1	99421	99423
NC_035780.1	99427	99429
NC_035780.1	99524	99526
NC_035780.1	586359	586361

==> 39F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-upstreamFlanks <==
NC_0


==> 54F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-upstreamFlanks <==
NC_007175.2	1658	1660
NC_007175.2	1749	1751
NC_007175.2	1766	1768
NC_007175.2	1825	1827
NC_007175.2	1836	1838
NC_007175.2	1842	1844
NC_007175.2	1846	1848
NC_007175.2	1854	1856
NC_007175.2	1873	1875
NC_007175.2	1918	1920

==> 54F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-upstreamFlanks <==
NC_035780.1	13485	13487
NC_035780.1	13513	13515
NC_035780.1	13527	13529
NC_035780.1	13561	13563
NC_035780.1	13564	13566
NC_035780.1	13571	13573
NC_035780.1	27979	27981
NC_035780.1	99371	99373
NC_035780.1	99376	99378
NC_035780.1	99421	99423

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-upstreamFlanks <==
NC_035780.1	253694	253696
NC_035780.1	314783	314785
NC_035780.1	314940	314942
NC_035780.1	314950	314952
NC_035780.1	314963	314965
NC_035780.1	314981	314983
NC_035780.1	314984	314986
NC_035780.1	604140	604142
NC_035780.1	604728	604730
NC_035780.1	604774	604776

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-upstreamFlanks <==
NC_


==> male-union-averages_10x.SNPcorr.bedgraph-lowMeth.bed-upstreamFlanks <==
NC_007175.2	1658	1660
NC_007175.2	1749	1751
NC_007175.2	1766	1768
NC_007175.2	1825	1827
NC_007175.2	1836	1838
NC_007175.2	1842	1844
NC_007175.2	1846	1848
NC_007175.2	1854	1856
NC_007175.2	1873	1875
NC_007175.2	1918	1920

==> male-union-averages_10x.SNPcorr.bedgraph-modMeth.bed-upstreamFlanks <==
NC_035780.1	99376	99378
NC_035780.1	99421	99423
NC_035780.1	99427	99429
NC_035780.1	253694	253696
NC_035780.1	253826	253828
NC_035780.1	253832	253834
NC_035780.1	253837	253839
NC_035780.1	253851	253853
NC_035780.1	253868	253870
NC_035780.1	253880	253882


In [38]:
#Count number of overlaps
!wc -l *upstreamFlanks

    8923 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-upstreamFlanks
  398939 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-upstreamFlanks
   12092 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-upstreamFlanks
    8730 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-upstreamFlanks
  398548 13M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-upstreamFlanks
   11624 13M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-upstreamFlanks
    7279 16F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-upstreamFlanks
  389917 16F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-upstreamFlanks
   13045 16F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-upstreamFlanks
    7176 19F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-upstreamFlanks
  392846 19F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-upstreamFlanks
   13657 19F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-upstreamFlanks
    6444 22F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-upstreamFlanks
  364931 22F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-upstreamFlanks
   11595 22F_R1_val_1_10x.SNPcorr.b

In [39]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-upstreamFlanks \
| sed '87,$ d' \
| awk '{print $1"\t"$2}' \
> upstreamFlanks-counts.txt

### 4g. Downstream flanks

In [40]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-features/C_virginica-3.0-downstream.gff \
    > ${f}-downstreamFlanks
done

In [41]:
#Check output
!head *downstreamFlanks

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-downstreamFlanks <==
NC_035780.1	106490	106492
NC_035780.1	257146	257148
NC_035780.1	257160	257162
NC_035780.1	257180	257182
NC_035780.1	257211	257213
NC_035780.1	257225	257227
NC_035780.1	257276	257278
NC_035780.1	257420	257422
NC_035780.1	257471	257473
NC_035780.1	257485	257487

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-downstreamFlanks <==
NC_007175.2	1658	1660
NC_007175.2	1749	1751
NC_007175.2	1766	1768
NC_007175.2	1825	1827
NC_007175.2	1836	1838
NC_007175.2	1842	1844
NC_007175.2	1846	1848
NC_007175.2	1854	1856
NC_007175.2	1873	1875
NC_007175.2	1918	1920

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-downstreamFlanks <==
NC_035780.1	106592	106594
NC_035780.1	157621	157623
NC_035780.1	257924	257926
NC_035780.1	257969	257971
NC_035780.1	257993	257995
NC_035780.1	258024	258026
NC_035780.1	258105	258107
NC_035780.1	294165	294167
NC_035780.1	294193	294195
NC_035780.1	312370	312372

==> 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-


==> 35F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-downstreamFlanks <==
NC_035780.1	106592	106594
NC_035780.1	257615	257617
NC_035780.1	294165	294167
NC_035780.1	312236	312238
NC_035780.1	312316	312318
NC_035780.1	312508	312510
NC_035780.1	340324	340326
NC_035780.1	340533	340535
NC_035780.1	341227	341229
NC_035780.1	341290	341292

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-downstreamFlanks <==
NC_035780.1	257146	257148
NC_035780.1	257160	257162
NC_035780.1	257180	257182
NC_035780.1	257211	257213
NC_035780.1	257225	257227
NC_035780.1	257471	257473
NC_035780.1	257485	257487
NC_035780.1	257505	257507
NC_035780.1	257536	257538
NC_035780.1	257550	257552

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-downstreamFlanks <==
NC_007175.2	1658	1660
NC_007175.2	1749	1751
NC_007175.2	1766	1768
NC_007175.2	1825	1827
NC_007175.2	1836	1838
NC_007175.2	1842	1844
NC_007175.2	1846	1848
NC_007175.2	1854	1856
NC_007175.2	1873	1875
NC_007175.2	1918	1920

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.


==> 53F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-downstreamFlanks <==
NC_007175.2	1658	1660
NC_007175.2	1749	1751
NC_007175.2	1766	1768
NC_007175.2	1825	1827
NC_007175.2	1836	1838
NC_007175.2	1842	1844
NC_007175.2	1846	1848
NC_007175.2	1854	1856
NC_007175.2	1873	1875
NC_007175.2	1918	1920

==> 53F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-downstreamFlanks <==
NC_035780.1	106592	106594
NC_035780.1	257160	257162
NC_035780.1	294193	294195
NC_035780.1	312370	312372
NC_035780.1	312427	312429
NC_035780.1	312508	312510
NC_035780.1	340533	340535
NC_035780.1	341290	341292
NC_035780.1	341419	341421
NC_035780.1	370701	370703

==> 54F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-downstreamFlanks <==
NC_035780.1	15353	15355
NC_035780.1	257146	257148
NC_035780.1	257160	257162
NC_035780.1	257180	257182
NC_035780.1	257471	257473
NC_035780.1	257485	257487
NC_035780.1	257505	257507
NC_035780.1	257601	257603
NC_035780.1	257615	257617
NC_035780.1	257666	257668

==> 54F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.be


==> fem-union-averages_10x.SNPcorr.bedgraph-Meth.bed-downstreamFlanks <==
NC_035780.1	15353	15355
NC_035780.1	257146	257148
NC_035780.1	257160	257162
NC_035780.1	257180	257182
NC_035780.1	257211	257213
NC_035780.1	257225	257227
NC_035780.1	257276	257278
NC_035780.1	257420	257422
NC_035780.1	257471	257473
NC_035780.1	257485	257487

==> fem-union-averages_10x.SNPcorr.bedgraph-lowMeth.bed-downstreamFlanks <==
NC_007175.2	1658	1660
NC_007175.2	1749	1751
NC_007175.2	1766	1768
NC_007175.2	1825	1827
NC_007175.2	1836	1838
NC_007175.2	1842	1844
NC_007175.2	1846	1848
NC_007175.2	1854	1856
NC_007175.2	1873	1875
NC_007175.2	1918	1920

==> fem-union-averages_10x.SNPcorr.bedgraph-modMeth.bed-downstreamFlanks <==
NC_035780.1	106490	106492
NC_035780.1	106592	106594
NC_035780.1	106647	106649
NC_035780.1	106720	106722
NC_035780.1	107170	107172
NC_035780.1	294020	294022
NC_035780.1	294095	294097
NC_035780.1	294165	294167
NC_035780.1	312427	312429
NC_035780.1	340324	340326

==> male-union-averages_10x-wb

In [42]:
#Count number of overlaps
!wc -l *downstreamFlanks

   37320 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-downstreamFlanks
  314909 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-downstreamFlanks
   24970 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-downstreamFlanks
   36396 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-downstreamFlanks
  313572 13M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-downstreamFlanks
   25158 13M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-downstreamFlanks
   32992 16F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-downstreamFlanks
  310859 16F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-downstreamFlanks
   27197 16F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-downstreamFlanks
   33724 19F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-downstreamFlanks
  313242 19F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-downstreamFlanks
   27810 19F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-downstreamFlanks
   30125 22F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-downstreamFlanks
  289686 22F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-downstreamFlanks
   2524

In [43]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-downstreamFlanks \
| sed '87,$ d' \
| awk '{print $1"\t"$2}' \
> downstreamFlanks-counts.txt

### 4h. Intergenic regions

In [44]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-features/C_virginica-3.0-intergenic.bed \
    > ${f}-intergenic
done

In [45]:
#Check output
!head *intergenic

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intergenic <==
NC_035780.1	114606	114608
NC_035780.1	114626	114628
NC_035780.1	114631	114633
NC_035780.1	114641	114643
NC_035780.1	123935	123937
NC_035780.1	256301	256303
NC_035780.1	256335	256337
NC_035780.1	256366	256368
NC_035780.1	256431	256433
NC_035780.1	256445	256447

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intergenic <==
NC_007175.2	6645	6647
NC_007175.2	6693	6695
NC_007175.2	6741	6743
NC_007175.2	6777	6779
NC_007175.2	6837	6839
NC_007175.2	6933	6935
NC_007175.2	6983	6985
NC_007175.2	6986	6988
NC_007175.2	7006	7008
NC_007175.2	7014	7016

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intergenic <==
NC_035780.1	11418	11420
NC_035780.1	11437	11439
NC_035780.1	11446	11448
NC_035780.1	11465	11467
NC_035780.1	16113	16115
NC_035780.1	16307	16309
NC_035780.1	16817	16819
NC_035780.1	21767	21769
NC_035780.1	23881	23883
NC_035780.1	23896	23898

==> 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intergenic <==
NC_035780.1	22531	22533


==> 36F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intergenic <==
NC_007175.2	6645	6647
NC_007175.2	6693	6695
NC_007175.2	6741	6743
NC_007175.2	6777	6779
NC_007175.2	6837	6839
NC_007175.2	6933	6935
NC_007175.2	6983	6985
NC_007175.2	6986	6988
NC_007175.2	7006	7008
NC_007175.2	7014	7016

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intergenic <==
NC_035780.1	1690	1692
NC_035780.1	1882	1884
NC_035780.1	9729	9731
NC_035780.1	15762	15764
NC_035780.1	16113	16115
NC_035780.1	22368	22370
NC_035780.1	22399	22401
NC_035780.1	22529	22531
NC_035780.1	22536	22538
NC_035780.1	23924	23926

==> 39F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intergenic <==
NC_035780.1	23863	23865
NC_035780.1	23889	23891
NC_035780.1	23892	23894
NC_035780.1	23896	23898
NC_035780.1	23900	23902
NC_035780.1	23924	23926
NC_035780.1	255018	255020
NC_035780.1	256025	256027
NC_035780.1	256027	256029
NC_035780.1	256045	256047

==> 39F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intergenic <==
NC_007175.2	6645	6647
NC_007175.2	669


==> 54F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intergenic <==
NC_035780.1	9637	9639
NC_035780.1	9657	9659
NC_035780.1	15762	15764
NC_035780.1	16307	16309
NC_035780.1	16355	16357
NC_035780.1	16632	16634
NC_035780.1	16817	16819
NC_035780.1	16941	16943
NC_035780.1	21582	21584
NC_035780.1	22368	22370

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intergenic <==
NC_035780.1	4959	4961
NC_035780.1	162436	162438
NC_035780.1	188647	188649
NC_035780.1	254242	254244
NC_035780.1	254295	254297
NC_035780.1	254312	254314
NC_035780.1	254334	254336
NC_035780.1	254488	254490
NC_035780.1	254501	254503
NC_035780.1	254589	254591

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intergenic <==
NC_007175.2	6645	6647
NC_007175.2	6693	6695
NC_007175.2	6741	6743
NC_007175.2	6777	6779
NC_007175.2	6837	6839
NC_007175.2	6933	6935
NC_007175.2	6983	6985
NC_007175.2	6986	6988
NC_007175.2	7006	7008
NC_007175.2	7014	7016

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intergenic <==
NC_035780.1	2783	2785
NC_03


==> male-union-averages_10x.SNPcorr.bedgraph-modMeth.bed-intergenic <==
NC_035780.1	15762	15764
NC_035780.1	16113	16115
NC_035780.1	16307	16309
NC_035780.1	16817	16819
NC_035780.1	21767	21769
NC_035780.1	22529	22531
NC_035780.1	22531	22533
NC_035780.1	22536	22538
NC_035780.1	22558	22560
NC_035780.1	22599	22601


In [46]:
#Count number of overlaps
!wc -l *intergenic

   82864 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intergenic
 2661064 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intergenic
  144577 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intergenic
   81106 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intergenic
 2656448 13M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intergenic
  148746 13M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intergenic
   68374 16F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intergenic
 2615631 16F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intergenic
  157994 16F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intergenic
   69424 19F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intergenic
 2614645 19F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intergenic
  159535 19F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intergenic
   60061 22F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-intergenic
 2358077 22F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-intergenic
  133343 22F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-intergenic
   86952 23M_R1_val_1_10x

In [57]:
#Get line counts for each fine
# Remove 87th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-intergenic \
| sed '87,$ d' \
| awk '{print $1"\t"$2}' \
> intergenic-counts.txt

### 4i. lncRNA

In [48]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-features/C_virginica-3.0-lncRNA.gff \
    > ${f}-lncRNA
done

In [49]:
#Check output
!head *lncRNA

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-lncRNA <==
NC_035780.1	4063991	4063993
NC_035780.1	4064152	4064154
NC_035780.1	4064204	4064206
NC_035780.1	4064327	4064329
NC_035780.1	4064368	4064370
NC_035780.1	4064560	4064562
NC_035780.1	4064643	4064645
NC_035780.1	4064663	4064665
NC_035780.1	4064802	4064804
NC_035780.1	4064937	4064939

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-lncRNA <==
NC_035780.1	13597	13599
NC_035780.1	13651	13653
NC_035780.1	13725	13727
NC_035780.1	14144	14146
NC_035780.1	169744	169746
NC_035780.1	169782	169784
NC_035780.1	900357	900359
NC_035780.1	900536	900538
NC_035780.1	900554	900556
NC_035780.1	900684	900686

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-lncRNA <==
NC_035780.1	14430	14432
NC_035780.1	14453	14455
NC_035780.1	2928624	2928626
NC_035780.1	2928793	2928795
NC_035780.1	2928841	2928843
NC_035780.1	2928879	2928881
NC_035780.1	2928904	2928906
NC_035780.1	2928939	2928941
NC_035780.1	2929150	2929152
NC_035780.1	2929153	2929155

==> 13M_R1_va


==> 35F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-lncRNA <==
NC_035780.1	13597	13599
NC_035780.1	13651	13653
NC_035780.1	13725	13727
NC_035780.1	14144	14146
NC_035780.1	900357	900359
NC_035780.1	900536	900538
NC_035780.1	900554	900556
NC_035780.1	900689	900691
NC_035780.1	900777	900779
NC_035780.1	900786	900788

==> 35F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-lncRNA <==
NC_035780.1	903251	903253
NC_035780.1	903331	903333
NC_035780.1	1435482	1435484
NC_035780.1	1435527	1435529
NC_035780.1	1435621	1435623
NC_035780.1	1435627	1435629
NC_035780.1	1437797	1437799
NC_035780.1	1437818	1437820
NC_035780.1	1437924	1437926
NC_035780.1	1437965	1437967

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-lncRNA <==
NC_035780.1	14453	14455
NC_035780.1	4063991	4063993
NC_035780.1	4064152	4064154
NC_035780.1	4064204	4064206
NC_035780.1	4064368	4064370
NC_035780.1	4064560	4064562
NC_035780.1	4064643	4064645
NC_035780.1	4064663	4064665
NC_035780.1	4064937	4064939
NC_035780.1	4065156	4065158

==> 36F_R1_v


==> 52F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-lncRNA <==
NC_035780.1	14430	14432
NC_035780.1	14453	14455
NC_035780.1	169622	169624
NC_035780.1	169636	169638
NC_035780.1	902108	902110
NC_035780.1	902112	902114
NC_035780.1	902128	902130
NC_035780.1	902499	902501
NC_035780.1	1435582	1435584
NC_035780.1	1435882	1435884

==> 53F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-lncRNA <==
NC_035780.1	4063991	4063993
NC_035780.1	4064152	4064154
NC_035780.1	4064204	4064206
NC_035780.1	4064327	4064329
NC_035780.1	4064368	4064370
NC_035780.1	4064560	4064562
NC_035780.1	4064643	4064645
NC_035780.1	4064663	4064665
NC_035780.1	4064937	4064939
NC_035780.1	4065156	4065158

==> 53F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-lncRNA <==
NC_035780.1	13597	13599
NC_035780.1	13651	13653
NC_035780.1	13725	13727
NC_035780.1	14144	14146
NC_035780.1	169622	169624
NC_035780.1	169636	169638
NC_035780.1	169744	169746
NC_035780.1	169782	169784
NC_035780.1	169888	169890
NC_035780.1	169922	169924

==> 53F_R1_val_1_10x.SNP


==> 9M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-lncRNA <==
NC_035780.1	4063991	4063993
NC_035780.1	4064152	4064154
NC_035780.1	4064204	4064206
NC_035780.1	4064327	4064329
NC_035780.1	4064368	4064370
NC_035780.1	4064560	4064562
NC_035780.1	4064643	4064645
NC_035780.1	4064663	4064665
NC_035780.1	4064802	4064804
NC_035780.1	4064937	4064939

==> 9M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-lncRNA <==
NC_035780.1	13597	13599
NC_035780.1	13651	13653
NC_035780.1	13725	13727
NC_035780.1	14144	14146
NC_035780.1	169744	169746
NC_035780.1	169782	169784
NC_035780.1	900357	900359
NC_035780.1	900536	900538
NC_035780.1	900554	900556
NC_035780.1	900684	900686

==> 9M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-lncRNA <==
NC_035780.1	14453	14455
NC_035780.1	1863246	1863248
NC_035780.1	1863289	1863291
NC_035780.1	1863324	1863326
NC_035780.1	1863341	1863343
NC_035780.1	1863470	1863472
NC_035780.1	1863507	1863509
NC_035780.1	2928904	2928906
NC_035780.1	4067987	4067989
NC_035780.1	4604757	4604759

==> fem-uni

In [50]:
#Count number of overlaps
!wc -l *lncRNA

   20265 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-lncRNA
  119817 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-lncRNA
   13452 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-lncRNA
   20886 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-lncRNA
  117246 13M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-lncRNA
   12202 13M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-lncRNA
   15329 16F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-lncRNA
  115485 16F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-lncRNA
   16501 16F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-lncRNA
   15164 19F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-lncRNA
  113777 19F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-lncRNA
   17070 19F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-lncRNA
   14828 22F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-lncRNA
  105846 22F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-lncRNA
   16126 22F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-lncRNA
   21511 23M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-lncRNA
  118492 23M_R1_val_1_10x.

In [51]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-lncRNA \
| sed '87,$ d' \
| awk '{print $1"\t"$2}' \
> lncRNA-counts.txt

### 4j. Transposable elements

In [52]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-features/C_virginica-3.0-rm.te.bed \
    > ${f}-TE
done

In [53]:
#Check output
!head *TE

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-TE <==
NC_035780.1	102592	102594
NC_035780.1	269593	269595
NC_035780.1	291998	292000
NC_035780.1	309317	309319
NC_035780.1	312893	312895
NC_035780.1	313036	313038
NC_035780.1	313191	313193
NC_035780.1	313262	313264
NC_035780.1	313426	313428
NC_035780.1	313601	313603

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-TE <==
NC_035780.1	8294	8296
NC_035780.1	10563	10565
NC_035780.1	10587	10589
NC_035780.1	16632	16634
NC_035780.1	37993	37995
NC_035780.1	38004	38006
NC_035780.1	38016	38018
NC_035780.1	38038	38040
NC_035780.1	38114	38116
NC_035780.1	38136	38138

==> 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-TE <==
NC_035780.1	328434	328436
NC_035780.1	328570	328572
NC_035780.1	328795	328797
NC_035780.1	380727	380729
NC_035780.1	380814	380816
NC_035780.1	476353	476355
NC_035780.1	476406	476408
NC_035780.1	479269	479271
NC_035780.1	479328	479330
NC_035780.1	479336	479338

==> 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-TE <==
NC_035780.1	26959


==> 36F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-TE <==
NC_035780.1	102592	102594
NC_035780.1	269593	269595
NC_035780.1	291998	292000
NC_035780.1	309317	309319
NC_035780.1	312893	312895
NC_035780.1	313036	313038
NC_035780.1	313191	313193
NC_035780.1	313262	313264
NC_035780.1	313426	313428
NC_035780.1	313601	313603

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-TE <==
NC_035780.1	8294	8296
NC_035780.1	10563	10565
NC_035780.1	10587	10589
NC_035780.1	16632	16634
NC_035780.1	37993	37995
NC_035780.1	38004	38006
NC_035780.1	38016	38018
NC_035780.1	38038	38040
NC_035780.1	38114	38116
NC_035780.1	38136	38138

==> 36F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-TE <==
NC_035780.1	328763	328765
NC_035780.1	394072	394074
NC_035780.1	394128	394130
NC_035780.1	476353	476355
NC_035780.1	476406	476408
NC_035780.1	479328	479330
NC_035780.1	479336	479338
NC_035780.1	479439	479441
NC_035780.1	479454	479456
NC_035780.1	576076	576078

==> 39F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-TE <==
NC_035780.1	1025


==> 54F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-TE <==
NC_035780.1	102592	102594
NC_035780.1	269593	269595
NC_035780.1	291998	292000
NC_035780.1	309317	309319
NC_035780.1	312893	312895
NC_035780.1	313036	313038
NC_035780.1	313191	313193
NC_035780.1	313262	313264
NC_035780.1	313426	313428
NC_035780.1	313841	313843

==> 54F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-TE <==
NC_035780.1	8294	8296
NC_035780.1	10563	10565
NC_035780.1	10587	10589
NC_035780.1	37993	37995
NC_035780.1	38004	38006
NC_035780.1	38016	38018
NC_035780.1	38038	38040
NC_035780.1	38114	38116
NC_035780.1	38136	38138
NC_035780.1	38162	38164

==> 54F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-TE <==
NC_035780.1	16632	16634
NC_035780.1	313601	313603
NC_035780.1	313725	313727
NC_035780.1	313740	313742
NC_035780.1	313760	313762
NC_035780.1	313909	313911
NC_035780.1	479269	479271
NC_035780.1	479328	479330
NC_035780.1	479439	479441
NC_035780.1	479454	479456

==> 59M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-TE <==
NC_035780.1	102592


==> fem-union-averages_10x.SNPcorr.bedgraph-Meth.bed-TE <==
NC_035780.1	269593	269595
NC_035780.1	291998	292000
NC_035780.1	309317	309319
NC_035780.1	312893	312895
NC_035780.1	313036	313038
NC_035780.1	313191	313193
NC_035780.1	313262	313264
NC_035780.1	313426	313428
NC_035780.1	313601	313603
NC_035780.1	313725	313727

==> fem-union-averages_10x.SNPcorr.bedgraph-lowMeth.bed-TE <==
NC_035780.1	8294	8296
NC_035780.1	10563	10565
NC_035780.1	10587	10589
NC_035780.1	16632	16634
NC_035780.1	37993	37995
NC_035780.1	38004	38006
NC_035780.1	38016	38018
NC_035780.1	38038	38040
NC_035780.1	38114	38116
NC_035780.1	38136	38138

==> fem-union-averages_10x.SNPcorr.bedgraph-modMeth.bed-TE <==
NC_035780.1	102592	102594
NC_035780.1	328434	328436
NC_035780.1	394072	394074
NC_035780.1	394123	394125
NC_035780.1	394128	394130
NC_035780.1	394195	394197
NC_035780.1	394270	394272
NC_035780.1	394286	394288
NC_035780.1	476353	476355
NC_035780.1	476406	476408

==> male-union-averages_10x-wb.bed-TE <==
NC_035780.

In [54]:
#Count number of overlaps
!wc -l *TE

   76717 12M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-TE
  198540 12M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-TE
   84484 12M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-TE
   76026 13M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-TE
  200817 13M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-TE
   89425 13M_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-TE
   65343 16F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-TE
  199413 16F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-TE
   80488 16F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-TE
   64942 19F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-TE
  202331 19F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-TE
   88955 19F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-TE
   57737 22F_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-TE
  177026 22F_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-TE
   62109 22F_R1_val_1_10x.SNPcorr.bedgraph-modMeth.bed-TE
   81468 23M_R1_val_1_10x.SNPcorr.bedgraph-Meth.bed-TE
  200369 23M_R1_val_1_10x.SNPcorr.bedgraph-lowMeth.bed-TE
   87364 23M_R1_val_1_10x.SNPcor

In [55]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-TE \
| sed '87,$ d' \
| awk '{print $1"\t"$2}' \
> TE-counts.txt